In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import numpy as np
import pandas as pd
import torch
import re
from sklearn.metrics import balanced_accuracy_score, roc_auc_score,accuracy_score,precision_recall_fscore_support
from Constants import *
from Preprocessing import *
from Models import *
import copy
from Utils import *
pd.set_option('display.max_rows', 200)



In [3]:
pd.read_csv('../data/digital_twin_ln_monograms.csv')

id  L1A  L1B  L2A  L2B   L3   L4  L5A  L5B   L6  ...  R1A  R1B  R2A  \
0        3  0.0  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
1        5  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
2        6  0.0  0.0  1.0  1.0  1.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
3        7  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
4        8  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
..     ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
531  10201  0.0  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   
532  10202  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
533  10203  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
534  10204  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  1.0   
535  10205  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0  0.0   

     R2B   R3   R4  R5A  R5B   R6  RRPLN  
0    0.0  0.0  0.0  0.0  0.0  0.0    0.0  
1    1.0  0.0  0.0  0.0  0.0  0.0    0.0  
2    1.0  1.0  0.0  0.0  0.0  0.0    0.0  
3    0.0  0.0  0.0  0.0  0.0  0.0    0.0  
4    1.0  0.0  0.0  0.0  0.0  0.0    0.0  
..   ...  ...  ...  ...  ...  ...    ...  
531  0.0  0.0  0.0  0.0  0.0  0.0    0.0  
532  1.0  0.0  0.0  0.0  0.0  0.0    0.0  
533  1.0  1.0  0.0  0.0  0.0  0.0    0.0  
534  1.0  1.0  0.0  0.0  0.0  0.0    0.0  
535  0.0  1.0  0.0  0.0  0.0  0.0    0.0  

[536 rows x 21 columns]

In [4]:
data = DTDataset(use_smote=True)
data.processed_df.T
# data.processed_df#.shape, len(data.processed_df.index.unique())

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


id                                    3      5          6          7      \
hpv                                       1      0          1          1   
age                               55.969444  20.95  69.930556  72.319444   
packs_per_year                          0.0   38.0       35.0        0.0   
gender                                    1      1          0          1   
smoking_status                          0.0    1.0        1.0        1.0   
Aspiration rate Pre-therapy               0      0          1          0   
total_dose                             66.0   72.0       70.0       70.0   
dose_fraction                           2.2    1.8   2.121212   2.121212   
bilateral                             False  False       True      False   
White/Caucasion                        True   True       True       True   
Hispanic/Latino                       False  False      False      False   
African American/Black                False  False      False      False   
Asian                                 False  False      False      False   
cc_none                                   0      0          0          1   
cc_platinum                               0      1          1          0   
cc_cetuximab                              1      0          0          0   
cc_others                                 0      0          0          0   
no_dose_adjustment                        1      1          1          1   
dose_modified                             0      0          0          0   
dose_delayed                              0      0          0          0   
dose_cancelled                            0      0          0          0   
dose_delayed_&_modified                   0      0          0          0   
regiment_modification                     0      0          0          0   
unknown                                   0      0          0          0   
T-category_1                              0      0          0          1   
T-category_2                              1      0          0          0   
T-category_3                              0      0          0          0   
T-category_4                              0      1          1          0   
N-category_0                              0      0          0          0   
N-category_1                              1      0          0          0   
N-category_2                              0      1          1          1   
N-category_3                              0      0          0          0   
AJCC_1                                    1      0          0          0   
AJCC_2                                    0      0          0          1   
AJCC_3                                    0      0          1          0   
AJCC_4                                    0      1          0          0   
Pathological Grade_0                      1      0          0          1   
Pathological Grade_1                      0      0          0          0   
Pathological Grade_2                      0      1          1          0   
Pathological Grade_3                      0      0          0          0   
Pathological Grade_4                      0      0          0          0   
subsite_BOT                               1      1          1          0   
subsite_GPS                               0      0          0          0   
subsite_NOS                               0      0          0          1   
subsite_Soft palate                       0      0          0          0   
subsite_Tonsil                            0      0          0          0   
treatment_CC                              1      1          1          0   
treatment_IC+CC                           0      0          0          0   
treatment_IC+Radiation alone              0      0          0          0   
treatment_Radiation alone                 0      0          0          1   
DLT_Dermatological                      0.0    0.0        0.0        0.0   
DLT_Neurological                        0.0    0

In [5]:
get_tt_split()[1]

[133,
 47,
 35,
 10,
 279,
 5056,
 5035,
 224,
 209,
 10063,
 2006,
 5020,
 271,
 10014,
 5080,
 10097,
 10125,
 10106,
 2032,
 10169,
 2024,
 286,
 2015,
 2019,
 10026,
 5040,
 236,
 187,
 10161,
 211,
 5103,
 10178,
 2026,
 10137,
 184,
 199,
 10040,
 272,
 68,
 5105,
 10177,
 228,
 44,
 242,
 9,
 5101,
 10104,
 10165,
 10007,
 10133,
 10145,
 10016,
 264,
 5098,
 10023,
 10050,
 5120,
 227,
 5118,
 2005,
 5053,
 10135,
 5007,
 10092,
 36,
 2001,
 5115,
 10005,
 10102,
 189,
 5036,
 10088,
 254,
 10130,
 10086,
 25,
 5001,
 5065,
 10084,
 195,
 5099,
 3,
 5093,
 10094,
 7,
 5038,
 10068,
 5032,
 202,
 274,
 45,
 2017,
 10176,
 217,
 10160,
 5082,
 10012,
 10017,
 10100,
 2031,
 77,
 10066,
 5078,
 117,
 10010,
 10170,
 10190,
 10058,
 5049,
 5086,
 5052,
 268,
 2029,
 5084,
 10105,
 10013,
 245,
 5048,
 2020,
 215,
 10046,
 5117,
 5033,
 267,
 5003,
 168,
 31,
 10049,
 10180,
 190,
 287,
 284,
 5054,
 10101,
 208,
 5077,
 10091,
 10172,
 288,
 5109,
 10126,
 10153,
 10123,
 5107,
 19

In [6]:
get_tt_split(resample_training=True)[0]

array([ 2023,    57, 10095,  5018,    18, 10003,   239, 10163,  5044,
        5075,  5100,   269, 10061, 10152, 10147,   218, 10163,    74,
       10082, 10164, 10114,  5104, 10025,  5023,  5058, 10132,   230,
       10073, 10015,  5100,   103,  5059,   282,  2028,  5030, 10074,
        2030,  5051,    64,  5021, 10164,    87, 10078,   256,    94,
        2027,   216,    38,    94, 10074,    40,   239,   289,   269,
        5069,    51,   252,  5074, 10045,    15, 10205,   237,  2033,
         280, 10117,  5021,  5072, 10109,     6, 10183,  5113, 10109,
       10083, 10195, 10078, 10043,   178,   241, 10138,  5031,    56,
        5005, 10022,  5074,    94,   200,   200, 10197,   213, 10148,
       10162,   206,  5014,   229, 10134, 10079,    32,    53,   257,
         231,   289,   249,  2022,   257, 10024,   210, 10081, 10071,
        2003, 10199,  2013,   229, 10195,  2011,  5055,   205,  5097,
       10111,    26, 10052, 10204,  2028, 10022,  5112, 10158, 10129,
       10197,    27,

In [33]:
def nllloss(ytrue,ypred):
    #nll loss with argmax added in
    loss = torch.nn.NLLLoss()
    return loss(ypred,ytrue.argmax(axis=1))

def state_loss(ytrue,ypred,weights=None):
    if weights is None:
        weights = [1,1,1,1]
    pd_loss = torch.mul(nllloss(ytrue[0],ypred[0]),weights[0])
    nd_loss = torch.mul(nllloss(ytrue[1],ypred[1]),weights[1])
    mod_loss = torch.mul(nllloss(ytrue[2],ypred[2]),weights[2])
    loss = torch.add(pd_loss,torch.add(nd_loss,mod_loss))
    dlt_true = ytrue[3]
    dlt_pred = ypred[3]
    ndlt = dlt_true.shape[1]
#     nloss = torch.nn.NLLLoss()
    bce = torch.nn.BCELoss()
    for i in range(ndlt):
        dlt_loss = bce(dlt_pred[:,i].view(-1),dlt_true[:,i].view(-1))
        dlt_loss = torch.mul(dlt_loss,weights[3]/ndlt)
        loss = torch.add(loss,dlt_loss)
    return loss

def outcome_loss(ytrue,ypred,weights=None):
    if weights is None:
        weights = [1,1,1,1]
    loss = 0
    nloss = torch.nn.BCELoss()
    for i in range(len(weights)):
        iloss = nloss(ypred[:,i],ytrue[i])*weights[i]
        loss += iloss
    return loss

def mc_metrics(yt,yp,numpy=False,is_dlt=False):
    if not numpy:
        yt = yt.cpu().detach().numpy()
        yp = yp.cpu().detach().numpy()
    #dlt prediction (binary)
    if is_dlt:
        acc = accuracy_score(yt,yp>.5)
        if yt.sum() > 1:
            try:
                auc = roc_auc_score(yt,yp)
            except:
                auc = -1
        else:
            auc=-1
        error = np.mean((yt-yp)**2)
        return {'accuracy': acc, 'mse': error, 'auc': auc}
    #this is a catch for when I se the dlt prediction format (encoded integer ordinal, predict as a categorical and take the argmax)
    elif yt.ndim > 1:
        try:
            bacc = balanced_accuracy_score(yt.argmax(axis=1),yp.argmax(axis=1))
        except:
            bacc = -1
        try:
            roc_micro = roc_auc_score(yt,yp,average='micro')
        except:
            roc_micro=-1
        try:
            roc_macro = roc_auc_score(yt,yp,average='macro')
        except Exception as e:
            try: 
                roc_macro = roc_auc_score(yt[:,0:2],yp[:,0:2],average='macro')
            except:
                roc_macro = -1
        try:
            roc_weighted = roc_auc_score(yt,yp,average='weighted')
        except:
            try:
                roc_weighted = roc_auc_score(yt[:,0:2],yp[:,0:2],average='weighted')
            except:
                roc_weighted= -1
        return {'accuracy': bacc, 'auc_micro': roc_micro,'auc_mean': roc_macro,'auc_weighted': roc_weighted}
    #outcomes (binary)
    else:
        multiclass = yp.ndim > 1
        if multiclass:
            yp = yp.argmax(axis=1)
        try:
            if not multiclass:
                bacc = accuracy_score(yt,(yp>.5).astype(int))
            else:
                bacc = accuracy_score(yt,yp)
        except Exception as e:
            print(e,yp,yt)
            bacc = -1
        try:
            roc = roc_auc_score(yt,yp)
        except:
            roc = -1
        try:
            if not multiclass:
                pr,re,fscore,supp = precision_recall_fscore_support(yt,(yp>.5).astype(int),average='binary')
            else:
                pr,re,fscore,supp = precision_recall_fscore_support(yt,yp,average='macro')
        except Exception as e:
            print(e)
            [pr,re,fscore,supp] = [-1,-1,-1,-1]
        error = np.mean((yt-yp)**2)
        return {'accuracy': bacc, 'mse': error, 'auc': roc,'precision': pr,'recall':re,'f1':fscore}

def state_metrics(ytrue,ypred,numpy=False):
    pd_metrics = mc_metrics(ytrue[0],ypred[0],numpy=numpy)
    nd_metrics = mc_metrics(ytrue[1],ypred[1],numpy=numpy)
    mod_metrics = mc_metrics(ytrue[1],ypred[1],numpy=numpy)
    
    dlt_metrics = []
    dlt_true = ytrue[3]
    dlt_pred = ypred[3]
    ndlt = dlt_true.shape[1]
    nloss = torch.nn.NLLLoss()
    for i in range(ndlt):
        dm = mc_metrics(dlt_true[:,i],dlt_pred[:,i].view(-1),is_dlt=True)
        dlt_metrics.append(dm)
    dlt_acc =[d['accuracy'] for d in dlt_metrics]
    dlt_error = [d['mse'] for d in dlt_metrics]
    dlt_auc = [d['auc'] for d in dlt_metrics]
    
    acc_mean = np.mean([a for a in dlt_acc if a >= 0 and a < 1])
    auc_mean = np.mean([a for a in dlt_auc if a >= 0])
    results = {'pd': pd_metrics,'nd': nd_metrics,'mod': mod_metrics,
               'dlts': {'accuracy': dlt_acc,'accuracy_mean': acc_mean,'auc': dlt_auc,'auc_mean': auc_mean}
              }
    return results

def outcome_metrics(ytrue,ypred,numpy=False):
    res = {}
    for i, outcome in enumerate(Const.outcomes):
        metrics = mc_metrics(ytrue[i],ypred[:,i])
        res[outcome] = metrics
    return res

def transition_sample(state):
    ids = get_dt_ids()
    
    train_ids, test_ids = get_tt_split()
    
    dataset = DTDataset()
    
    #only train on people with  IC for state 1 since other people can't have any outcomes otherwise
    require = None
    if state == 1:
        require = Const.decisions[0] #we don't expect a state update if there is no treatment
        valid_ids = dataset.get_input_state(require=require).index.values
        train_ids = [t for t in train_ids if t in valid_ids]
        test_ids = [t for t in test_ids if t in valid_ids]
    xtrain = dataset.get_input_state(step=state,ids=train_ids,require=require)
    xtest = dataset.get_input_state(step=state,ids=test_ids,require=require)
    ytrain = dataset.get_intermediate_outcomes(step=state,ids=train_ids,require=require)
    ytest = dataset.get_intermediate_outcomes(step=state,ids=test_ids,require=require)

    xtrain = df_to_torch(xtrain)
    xtest = df_to_torch(xtest)
    ytrain = [df_to_torch(t) for t in ytrain]
    ytest= [df_to_torch(t) for t in ytest]
    return xtrain,xtest,ytrain,ytest

In [162]:
def train_state(model=None,
                model_args={},
                state=1,
                split=.7,
                lr=.001,
                epochs=1000,
                patience=10,
                use_attention=False,
                weights=None,
                save_path='../data/models/',
                use_default_split=True,
                use_bagging_split=False,
                resample_training=False,#use bootstraping on training data after splitting
                n_validation_trainsteps=2,
                verbose=True,
                use_smote=False,
                smote_cols = None,
                file_suffix=''):
    
    ids = get_dt_ids()
    
    train_ids, test_ids = get_tt_split(use_default_split=use_default_split,use_bagging_split=use_bagging_split,resample_training=resample_training)

    if use_smote:
        if smote_cols is None:
            smote_cols = Const.outcomes
            if state == 1:
                smote_cols = Const.primary_disease_states
            elif state == 2:
                smote_cols = Const.primary_disease_states2
        dataset = DTDataset(use_smote=True,smote_ids = train_ids,smote_columns=[Const.decisions[state-1]])
        train_ids = [i for i in dataset.processed_df.index.values if i not in test_ids]
    else:
        dataset = DTDataset()
    
    #only train on people with  IC for state 1 since other people can't have any outcomes otherwise
    require = None
    if state == 1:
        require = Const.decisions[0] #we don't expect a state update if there is no treatment
        valid_ids = dataset.get_input_state(require=require).index.values
        train_ids = [t for t in train_ids if t in valid_ids]
        test_ids = [t for t in test_ids if t in valid_ids]
    xtrain = dataset.get_input_state(step=state,ids=train_ids,require=require)
    xtest = dataset.get_input_state(step=state,ids=test_ids,require=require)
    ytrain = dataset.get_intermediate_outcomes(step=state,ids=train_ids,require=require)
    ytest = dataset.get_intermediate_outcomes(step=state,ids=test_ids,require=require)
    

    if not use_attention:
        model_args = {k:v for k,v in model_args.items() if 'attention' not in k and 'embed_size' not in k}
    if state < 3:
        if model is None:
            if use_attention:
                model = OutcomeAttentionSimulator(xtrain.shape[1],state=state,**model_args)
            else:
                model = OutcomeSimulator(xtrain.shape[1],state=state,**model_args)
        lfunc = state_loss
        if weights is None:
            weights = [1,1,.1,1]
    else:
        if model is None:
            if use_attention:
                model = EndpointAttentionSimulator(xtrain.shape[1],**model_args)
            else:
                model = EndpointSimulator(xtrain.shape[1],**model_args)
        if weights is None:
            weights = [1,1,1,1]
        lfunc = outcome_loss
        
    device = 'cuda' if torch.cuda.is_available() else 'cpu'
    model.set_device(device)
    
    hashcode = str(hash(','.join([str(i) for i in train_ids])))
    save_file = save_path + 'model_' + model.identifier + '_split' + str(split) + '_resample' + str(resample_training) +  '_hash' + hashcode + file_suffix + '.tar'
    xtrain = df_to_torch(xtrain).to(device)
    if use_attention:
        model.save_memory(xtrain)
    xtest = df_to_torch(xtest).to(device)
    ytrain = [df_to_torch(t).to(device) for t in ytrain]
    ytest= [df_to_torch(t).to(device) for t in ytest]
    
    model.fit_normalizer(xtrain)
#     normalize = lambda x: (x - xtrain.mean(axis=0)+.01)/(xtrain.std(axis=0)+.01)
#     unnormalize = lambda x: (x * (xtrain.std(axis=0) +.01)) + xtrain.mean(axis=0) - .01
    
    optimizer = torch.optim.Adam(model.parameters(),lr=lr)
    best_val_loss = 1000000000000000000000000000
    best_loss_metrics = {}
    last_epoch = False
    for epoch in range(epochs):
        
        model.train(True)
        optimizer.zero_grad()
        
        xtrain_sample = xtrain#[torch.randint(len(xtrain),(len(xtrain),) )]
        ypred = model(xtrain_sample)
        loss = lfunc(ytrain,ypred,weights=weights)

        loss.backward()
        optimizer.step()
        if verbose:
            print('epoch',epoch,'train loss',loss.item())
        
        model.eval()
        if use_attention:
            yval = model(xtest,use_saved_memory=True)
        else:
            yval = model(xtest)
        val_loss = lfunc(ytest,yval,weights=weights)
        if state < 3:
            val_metrics = state_metrics(ytest,yval)
        else:
            val_metrics = outcome_metrics(ytest,yval)
        if val_loss.item() < best_val_loss:
            best_val_loss = val_loss.item()
            best_loss_metrics = val_metrics
            steps_since_improvement = 0
            torch.save(model.state_dict(),save_file)
        else:
            steps_since_improvement += 1
        if verbose:
            print('val loss',val_loss.item())
            print('______________')
        if steps_since_improvement > patience:
            break
    print('best loss',best_val_loss,best_loss_metrics)
    model.load_state_dict(torch.load(save_file))
    
    #train one step on validation data
    for i in range(n_validation_trainsteps):
        model.train()
        yval = model(xtest)
        val_loss = lfunc(ytest,yval,weights=weights)
        val_loss.backward()
        optimizer.step()
        torch.save(model.state_dict(),save_file)
    
    model.eval()
    return model,  best_val_loss, best_loss_metrics

t1_args = {'hidden_layers': [100],
   'dropout': 0.1,
   'input_dropout': 0.1}
train_state(model_args=t1_args,lr=.0001,weights=[1,1,.1,.1],use_attention=False)

epoch 0 train loss 2.4797959327697754
val loss 2.488689661026001
______________
epoch 1 train loss 2.4848880767822266
val loss 2.4858312606811523
______________
epoch 2 train loss 2.4789881706237793
val loss 2.4829962253570557
______________
epoch 3 train loss 2.4794230461120605
val loss 2.480158805847168
______________
epoch 4 train loss 2.4735381603240967
val loss 2.4773223400115967
______________
epoch 5 train loss 2.4638779163360596
val loss 2.4744932651519775
______________
epoch 6 train loss 2.4587671756744385
val loss 2.4716696739196777
______________
epoch 7 train loss 2.445873975753784
val loss 2.4688520431518555
______________
epoch 8 train loss 2.4561190605163574
val loss 2.4660356044769287
______________
epoch 9 train loss 2.4536471366882324
val loss 2.4632315635681152
______________
epoch 10 train loss 2.4480741024017334
val loss 2.4604318141937256
______________
epoch 11 train loss 2.4473767280578613
val loss 2.457636833190918
______________
epoch 12 train loss 2.44489216

epoch 105 train loss 2.1542303562164307
val loss 2.218567132949829
______________
epoch 106 train loss 2.1576740741729736
val loss 2.2161900997161865
______________
epoch 107 train loss 2.1522786617279053
val loss 2.2138142585754395
______________
epoch 108 train loss 2.15812349319458
val loss 2.211446762084961
______________
epoch 109 train loss 2.1452624797821045
val loss 2.2090864181518555
______________
epoch 110 train loss 2.1516690254211426
val loss 2.206733465194702
______________
epoch 111 train loss 2.1442413330078125
val loss 2.2043917179107666
______________
epoch 112 train loss 2.1260249614715576
val loss 2.2020537853240967
______________
epoch 113 train loss 2.135693073272705
val loss 2.1997177600860596
______________
epoch 114 train loss 2.127131938934326
val loss 2.1973793506622314
______________
epoch 115 train loss 2.1334400177001953
val loss 2.195044994354248
______________
epoch 116 train loss 2.128418207168579
val loss 2.1927146911621094
______________
epoch 117 tra

epoch 208 train loss 1.8559337854385376
val loss 1.9900861978530884
______________
epoch 209 train loss 1.8633701801300049
val loss 1.9880931377410889
______________
epoch 210 train loss 1.8540866374969482
val loss 1.9861164093017578
______________
epoch 211 train loss 1.8513633012771606
val loss 1.9841392040252686
______________
epoch 212 train loss 1.8483327627182007
val loss 1.9821703433990479
______________
epoch 213 train loss 1.8654568195343018
val loss 1.9802056550979614
______________
epoch 214 train loss 1.843903660774231
val loss 1.978249430656433
______________
epoch 215 train loss 1.8371798992156982
val loss 1.9763050079345703
______________
epoch 216 train loss 1.851418375968933
val loss 1.9743560552597046
______________
epoch 217 train loss 1.838580846786499
val loss 1.9724067449569702
______________
epoch 218 train loss 1.8330951929092407
val loss 1.9704636335372925
______________
epoch 219 train loss 1.8395960330963135
val loss 1.9685264825820923
______________
epoch 22

epoch 310 train loss 1.6194943189620972
val loss 1.8253270387649536
______________
epoch 311 train loss 1.6144134998321533
val loss 1.824172854423523
______________
epoch 312 train loss 1.5880935192108154
val loss 1.8230258226394653
______________
epoch 313 train loss 1.5998433828353882
val loss 1.8218953609466553
______________
epoch 314 train loss 1.5941962003707886
val loss 1.820770502090454
______________
epoch 315 train loss 1.5969622135162354
val loss 1.8196437358856201
______________
epoch 316 train loss 1.5880768299102783
val loss 1.8185080289840698
______________
epoch 317 train loss 1.6077072620391846
val loss 1.8173749446868896
______________
epoch 318 train loss 1.5940440893173218
val loss 1.8162587881088257
______________
epoch 319 train loss 1.5898336172103882
val loss 1.8151566982269287
______________
epoch 320 train loss 1.5841715335845947
val loss 1.8140689134597778
______________
epoch 321 train loss 1.5917457342147827
val loss 1.8129990100860596
______________
epoch 

val loss 1.7500979900360107
______________
epoch 415 train loss 1.4444971084594727
val loss 1.7497940063476562
______________
epoch 416 train loss 1.416691541671753
val loss 1.7495070695877075
______________
epoch 417 train loss 1.4034467935562134
val loss 1.7492235898971558
______________
epoch 418 train loss 1.4374390840530396
val loss 1.7489527463912964
______________
epoch 419 train loss 1.416170597076416
val loss 1.7486698627471924
______________
epoch 420 train loss 1.416592001914978
val loss 1.7483772039413452
______________
epoch 421 train loss 1.4118812084197998
val loss 1.74808931350708
______________
epoch 422 train loss 1.4292079210281372
val loss 1.7478026151657104
______________
epoch 423 train loss 1.391079068183899
val loss 1.7475098371505737
______________
epoch 424 train loss 1.4164265394210815
val loss 1.7472337484359741
______________
epoch 425 train loss 1.4090031385421753
val loss 1.746975302696228
______________
epoch 426 train loss 1.426762580871582
val loss 1.7

(OutcomeSimulator(
   (input_dropout): Dropout(p=0.1, inplace=False)
   (layers): ModuleList(
     (0): Linear(in_features=56, out_features=100, bias=True)
     (1): ReLU()
   )
   (batchnorm): BatchNorm1d(100, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
   (dropout): Dropout(p=0.1, inplace=False)
   (relu): Softplus(beta=1, threshold=20)
   (sigmoid): Sigmoid()
   (softmax): LogSoftmax(dim=1)
   (disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (nodal_disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (dlt_layers): ModuleList(
     (0-7): 8 x Linear(in_features=100, out_features=1, bias=True)
   )
   (treatment_layer): Linear(in_features=100, out_features=7, bias=True)
 ),
 1.740195393562317,
 {'pd': {'accuracy': 0.3890476190476191,
   'auc_micro': 0.7793367346938777,
   'auc_mean': 0.6209014104518369,
   'auc_weighted': 0.6537029086041878},
  'nd': {'accuracy': 0.3333333333333333,
   'auc_micro': 0.8390188434048084,
   'auc_

In [163]:
train_state(model_args=t1_args,lr=.0001,weights=[1,1,.1,.1],use_attention=False,use_smote=True)

here
epoch 0 train loss 2.4406609535217285


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


val loss 2.400536298751831
______________
epoch 1 train loss 2.4315595626831055
val loss 2.3974504470825195
______________
epoch 2 train loss 2.4319140911102295
val loss 2.3943514823913574
______________
epoch 3 train loss 2.430854082107544
val loss 2.3912580013275146
______________
epoch 4 train loss 2.425145149230957
val loss 2.3881711959838867
______________
epoch 5 train loss 2.418604850769043
val loss 2.3851001262664795
______________
epoch 6 train loss 2.415682077407837
val loss 2.382045269012451
______________
epoch 7 train loss 2.4148941040039062
val loss 2.378994941711426
______________
epoch 8 train loss 2.4119791984558105
val loss 2.3759496212005615
______________
epoch 9 train loss 2.405241012573242
val loss 2.372908353805542
______________
epoch 10 train loss 2.4018759727478027
val loss 2.369877815246582
______________
epoch 11 train loss 2.4061832427978516
val loss 2.3668572902679443
______________
epoch 12 train loss 2.401031732559204
val loss 2.36384654045105
__________

val loss 2.1182491779327393
______________
epoch 103 train loss 2.1104347705841064
val loss 2.1157376766204834
______________
epoch 104 train loss 2.113450288772583
val loss 2.113231897354126
______________
epoch 105 train loss 2.108124017715454
val loss 2.110729217529297
______________
epoch 106 train loss 2.10797119140625
val loss 2.10823917388916
______________
epoch 107 train loss 2.0997185707092285
val loss 2.105757236480713
______________
epoch 108 train loss 2.097209930419922
val loss 2.103278160095215
______________
epoch 109 train loss 2.09559965133667
val loss 2.1008033752441406
______________
epoch 110 train loss 2.093993902206421
val loss 2.098335027694702
______________
epoch 111 train loss 2.0916378498077393
val loss 2.0958750247955322
______________
epoch 112 train loss 2.0839428901672363
val loss 2.0934205055236816
______________
epoch 113 train loss 2.0809500217437744
val loss 2.0909698009490967
______________
epoch 114 train loss 2.0859248638153076
val loss 2.08852362

val loss 1.8925747871398926
______________
epoch 205 train loss 1.8169535398483276
val loss 1.8907334804534912
______________
epoch 206 train loss 1.8130077123641968
val loss 1.888893723487854
______________
epoch 207 train loss 1.8167622089385986
val loss 1.8870741128921509
______________
epoch 208 train loss 1.8048555850982666
val loss 1.8852696418762207
______________
epoch 209 train loss 1.8146992921829224
val loss 1.8834755420684814
______________
epoch 210 train loss 1.819361686706543
val loss 1.8816888332366943
______________
epoch 211 train loss 1.8036994934082031
val loss 1.8799079656600952
______________
epoch 212 train loss 1.806906819343567
val loss 1.878134846687317
______________
epoch 213 train loss 1.8045389652252197
val loss 1.8763649463653564
______________
epoch 214 train loss 1.7909692525863647
val loss 1.8746057748794556
______________
epoch 215 train loss 1.811452865600586
val loss 1.8728535175323486
______________
epoch 216 train loss 1.7967640161514282
val loss 

val loss 1.749107837677002
______________
epoch 308 train loss 1.5934797525405884
val loss 1.748168706893921
______________
epoch 309 train loss 1.5826793909072876
val loss 1.7472292184829712
______________
epoch 310 train loss 1.5837666988372803
val loss 1.7463130950927734
______________
epoch 311 train loss 1.5875526666641235
val loss 1.745412826538086
______________
epoch 312 train loss 1.574502944946289
val loss 1.7445080280303955
______________
epoch 313 train loss 1.582520604133606
val loss 1.743604063987732
______________
epoch 314 train loss 1.573137640953064
val loss 1.7427102327346802
______________
epoch 315 train loss 1.5716980695724487
val loss 1.7418211698532104
______________
epoch 316 train loss 1.563704252243042
val loss 1.74094820022583
______________
epoch 317 train loss 1.567240595817566
val loss 1.7400805950164795
______________
epoch 318 train loss 1.5545837879180908
val loss 1.7392067909240723
______________
epoch 319 train loss 1.5473642349243164
val loss 1.7383

epoch 408 train loss 1.4224956035614014
val loss 1.6937057971954346
______________
epoch 409 train loss 1.4129925966262817
val loss 1.6934759616851807
______________
epoch 410 train loss 1.418999195098877
val loss 1.6932520866394043
______________
epoch 411 train loss 1.404797077178955
val loss 1.693032145500183
______________
epoch 412 train loss 1.4208574295043945
val loss 1.692813754081726
______________
epoch 413 train loss 1.4001176357269287
val loss 1.6925913095474243
______________
epoch 414 train loss 1.398234486579895
val loss 1.692376971244812
______________
epoch 415 train loss 1.413993239402771
val loss 1.692179560661316
______________
epoch 416 train loss 1.4106839895248413
val loss 1.6920067071914673
______________
epoch 417 train loss 1.3912339210510254
val loss 1.6918420791625977
______________
epoch 418 train loss 1.4188764095306396
val loss 1.6916810274124146
______________
epoch 419 train loss 1.3995484113693237
val loss 1.6915167570114136
______________
epoch 420 tr

(OutcomeSimulator(
   (input_dropout): Dropout(p=0.1, inplace=False)
   (layers): ModuleList(
     (0): Linear(in_features=56, out_features=100, bias=True)
     (1): ReLU()
   )
   (batchnorm): BatchNorm1d(100, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
   (dropout): Dropout(p=0.1, inplace=False)
   (relu): Softplus(beta=1, threshold=20)
   (sigmoid): Sigmoid()
   (softmax): LogSoftmax(dim=1)
   (disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (nodal_disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (dlt_layers): ModuleList(
     (0-7): 8 x Linear(in_features=100, out_features=1, bias=True)
   )
   (treatment_layer): Linear(in_features=100, out_features=7, bias=True)
 ),
 1.6884554624557495,
 {'pd': {'accuracy': 0.40238095238095234,
   'auc_micro': 0.7855548469387755,
   'auc_mean': 0.6127092041700867,
   'auc_weighted': 0.6628366072192546},
  'nd': {'accuracy': 0.3333333333333333,
   'auc_micro': 0.857050032488629,
   'auc

In [164]:
train_state(model_args=t1_args,state=2,lr=.001,weights=[1,1,.1,10],use_smote=False)

epoch 0 train loss 7.890143394470215
val loss 8.179377555847168
______________
epoch 1 train loss 7.742368698120117
val loss 8.031600952148438
______________
epoch 2 train loss 7.605949878692627
val loss 7.8877410888671875
______________
epoch 3 train loss 7.466205596923828
val loss 7.747334003448486
______________
epoch 4 train loss 7.334397315979004
val loss 7.610104084014893
______________
epoch 5 train loss 7.209589958190918
val loss 7.4757561683654785
______________
epoch 6 train loss 7.068554878234863
val loss 7.343966007232666
______________
epoch 7 train loss 6.956936836242676
val loss 7.214866638183594
______________
epoch 8 train loss 6.839738368988037
val loss 7.0876970291137695
______________
epoch 9 train loss 6.705082416534424
val loss 6.96211051940918
______________
epoch 10 train loss 6.578567028045654
val loss 6.837925434112549
______________
epoch 11 train loss 6.46657657623291
val loss 6.715025424957275
______________
epoch 12 train loss 6.359525680541992
val loss 6.

epoch 104 train loss 1.9348517656326294
val loss 2.6318397521972656
______________
epoch 105 train loss 1.9012534618377686
val loss 2.630516290664673
______________
epoch 106 train loss 1.933562994003296
val loss 2.6299901008605957
______________
epoch 107 train loss 1.9227371215820312
val loss 2.6292507648468018
______________
epoch 108 train loss 1.894158124923706
val loss 2.62846040725708
______________
epoch 109 train loss 1.9202680587768555
val loss 2.627748489379883
______________
epoch 110 train loss 1.8900082111358643
val loss 2.6271140575408936
______________
epoch 111 train loss 1.9138238430023193
val loss 2.626497745513916
______________
epoch 112 train loss 1.901793360710144
val loss 2.6257264614105225
______________
epoch 113 train loss 1.869400143623352
val loss 2.625408411026001
______________
epoch 114 train loss 1.8833131790161133
val loss 2.625779628753662
______________
epoch 115 train loss 1.8339396715164185
val loss 2.6260604858398438
______________
epoch 116 train

(OutcomeSimulator(
   (input_dropout): Dropout(p=0.1, inplace=False)
   (layers): ModuleList(
     (0): Linear(in_features=78, out_features=100, bias=True)
     (1): ReLU()
   )
   (batchnorm): BatchNorm1d(100, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
   (dropout): Dropout(p=0.1, inplace=False)
   (relu): Softplus(beta=1, threshold=20)
   (sigmoid): Sigmoid()
   (softmax): LogSoftmax(dim=1)
   (disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (nodal_disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (dlt_layers): ModuleList(
     (0-7): 8 x Linear(in_features=100, out_features=1, bias=True)
   )
   (treatment_layer): Linear(in_features=100, out_features=4, bias=True)
 ),
 2.6248345375061035,
 {'pd': {'accuracy': 0.3333333333333333,
   'auc_micro': 0.9257856341189674,
   'auc_mean': 0.6922324225380097,
   'auc_weighted': 0.7171694270758755},
  'nd': {'accuracy': 0.33197013956507626,
   'auc_micro': 0.7413146654010441,
   'au

In [165]:
train_state(model_args=t1_args,state=2,lr=.001,weights=[1,1,.1,10],use_smote=True)

here
epoch 0 train loss 6.484133243560791
val loss 7.773698806762695
______________
epoch 1 train loss 6.366229057312012


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


val loss 7.6201276779174805
______________
epoch 2 train loss 6.230362892150879
val loss 7.469916343688965
______________
epoch 3 train loss 6.120296478271484
val loss 7.322803974151611
______________
epoch 4 train loss 5.9951558113098145
val loss 7.178547382354736
______________
epoch 5 train loss 5.88148307800293
val loss 7.036961555480957
______________
epoch 6 train loss 5.7552809715271
val loss 6.897736072540283
______________
epoch 7 train loss 5.648528099060059
val loss 6.760365962982178
______________
epoch 8 train loss 5.531651020050049
val loss 6.62467622756958
______________
epoch 9 train loss 5.425045967102051
val loss 6.490564823150635
______________
epoch 10 train loss 5.302168369293213
val loss 6.357881546020508
______________
epoch 11 train loss 5.200235843658447
val loss 6.226449966430664
______________
epoch 12 train loss 5.102266788482666
val loss 6.096390247344971
______________
epoch 13 train loss 4.979338645935059
val loss 5.967426300048828
______________
epoch 14

val loss 2.616286039352417
______________
epoch 104 train loss 1.6402289867401123
val loss 2.6160061359405518
______________
epoch 105 train loss 1.615355134010315
val loss 2.615922212600708
______________
epoch 106 train loss 1.6154911518096924
val loss 2.616138219833374
______________
epoch 107 train loss 1.6167793273925781
val loss 2.616459369659424
______________
epoch 108 train loss 1.6017327308654785
val loss 2.616960287094116
______________
epoch 109 train loss 1.6149059534072876
val loss 2.6174864768981934
______________
epoch 110 train loss 1.5868438482284546
val loss 2.618065357208252
______________
epoch 111 train loss 1.5731737613677979
val loss 2.618867874145508
______________
epoch 112 train loss 1.5880426168441772
val loss 2.6197099685668945
______________
epoch 113 train loss 1.5655879974365234
val loss 2.620704412460327
______________
epoch 114 train loss 1.5748170614242554
val loss 2.6219255924224854
______________
epoch 115 train loss 1.5652071237564087
val loss 2.62

(OutcomeSimulator(
   (input_dropout): Dropout(p=0.1, inplace=False)
   (layers): ModuleList(
     (0): Linear(in_features=78, out_features=100, bias=True)
     (1): ReLU()
   )
   (batchnorm): BatchNorm1d(100, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
   (dropout): Dropout(p=0.1, inplace=False)
   (relu): Softplus(beta=1, threshold=20)
   (sigmoid): Sigmoid()
   (softmax): LogSoftmax(dim=1)
   (disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (nodal_disease_layer): Linear(in_features=100, out_features=3, bias=True)
   (dlt_layers): ModuleList(
     (0-7): 8 x Linear(in_features=100, out_features=1, bias=True)
   )
   (treatment_layer): Linear(in_features=100, out_features=4, bias=True)
 ),
 2.615922212600708,
 {'pd': {'accuracy': 0.3333333333333333,
   'auc_micro': 0.9259493078937523,
   'auc_mean': 0.7169315437501429,
   'auc_weighted': 0.7294789031549807},
  'nd': {'accuracy': 0.32534891269068483,
   'auc_micro': 0.7383958234456574,
   'auc

In [166]:
train_state(model_args=t1_args,state=3,lr=.001,weights=[1,1,1,1],use_smote=False)

epoch 0 train loss 2.9423484802246094
val loss 2.863138198852539
______________
epoch 1 train loss 2.8763628005981445
val loss 2.807602882385254
______________
epoch 2 train loss 2.8245556354522705
val loss 2.7538299560546875
______________
epoch 3 train loss 2.7716121673583984
val loss 2.7015633583068848
______________
epoch 4 train loss 2.7074646949768066
val loss 2.6507511138916016
______________
epoch 5 train loss 2.677123785018921
val loss 2.6012916564941406
______________
epoch 6 train loss 2.6123905181884766
val loss 2.553199052810669
______________
epoch 7 train loss 2.5674238204956055
val loss 2.506574869155884
______________
epoch 8 train loss 2.515899658203125
val loss 2.4612574577331543
______________
epoch 9 train loss 2.470343589782715
val loss 2.4171764850616455
______________
epoch 10 train loss 2.417858600616455
val loss 2.3743155002593994
______________
epoch 11 train loss 2.3724632263183594
val loss 2.332658052444458
______________
epoch 12 train loss 2.3359403610229

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

val loss 1.8964873552322388
______________
epoch 25 train loss 1.8654839992523193
val loss 1.8711079359054565
______________
epoch 26 train loss 1.8393502235412598
val loss 1.8469253778457642
______________
epoch 27 train loss 1.809281826019287
val loss 1.823900580406189
______________
epoch 28 train loss 1.7836127281188965
val loss 1.8021142482757568
______________
epoch 29 train loss 1.7472690343856812
val loss 1.7815032005310059
______________
epoch 30 train loss 1.738081693649292
val loss 1.7621793746948242
______________
epoch 31 train loss 1.7003896236419678
val loss 1.744096279144287
______________
epoch 32 train loss 1.692948818206787
val loss 1.7271933555603027
______________
epoch 33 train loss 1.6686128377914429
val loss 1.7114336490631104
______________
epoch 34 train loss 1.645845890045166
val loss 1.6968199014663696
______________
epoch 35 train loss 1.6357979774475098
val loss 1.6832938194274902
______________
epoch 36 train loss 1.6103579998016357
val loss 1.67084527015

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

val loss 1.6594178676605225
______________
epoch 38 train loss 1.5556023120880127
val loss 1.6489439010620117
______________
epoch 39 train loss 1.5558243989944458
val loss 1.6393826007843018
______________
epoch 40 train loss 1.5594286918640137
val loss 1.6306920051574707
______________
epoch 41 train loss 1.5337367057800293
val loss 1.622838020324707
______________
epoch 42 train loss 1.5313130617141724
val loss 1.61576509475708
______________
epoch 43 train loss 1.5126205682754517
val loss 1.6094352006912231
______________
epoch 44 train loss 1.496941328048706
val loss 1.6037774085998535
______________
epoch 45 train loss 1.4844876527786255
val loss 1.598684549331665
______________
epoch 46 train loss 1.4679204225540161
val loss 1.5942294597625732
______________
epoch 47 train loss 1.4593932628631592
val loss 1.5904018878936768
______________
epoch 48 train loss 1.451768159866333
val loss 1.5871350765228271
______________
epoch 49 train loss 1.452231526374817
val loss 1.584269404411

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

val loss 1.5818467140197754
______________
epoch 51 train loss 1.427962064743042
val loss 1.579831600189209
______________
epoch 52 train loss 1.4226555824279785
val loss 1.5781511068344116
______________
epoch 53 train loss 1.4139516353607178
val loss 1.5767771005630493
______________
epoch 54 train loss 1.4244098663330078
val loss 1.5757052898406982
______________
epoch 55 train loss 1.410422682762146
val loss 1.5749410390853882
______________
epoch 56 train loss 1.4185857772827148
val loss 1.5744946002960205
______________
epoch 57 train loss 1.3838257789611816
val loss 1.5742079019546509
______________
epoch 58 train loss 1.3863370418548584
val loss 1.5741064548492432
______________
epoch 59 train loss 1.3791791200637817
val loss 1.574082612991333
______________
epoch 60 train loss 1.37173330783844
val loss 1.574255347251892
______________
epoch 61 train loss 1.3521090745925903
val loss 1.5745902061462402
______________
epoch 62 train loss 1.3598289489746094
val loss 1.575035095214

(EndpointSimulator(
   (input_dropout): Dropout(p=0.1, inplace=False)
   (layers): ModuleList(
     (0): Linear(in_features=76, out_features=100, bias=True)
     (1): ReLU()
   )
   (batchnorm): BatchNorm1d(100, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
   (dropout): Dropout(p=0.1, inplace=False)
   (relu): Softplus(beta=1, threshold=20)
   (sigmoid): Sigmoid()
   (softmax): LogSoftmax(dim=1)
   (outcome_layer): Linear(in_features=100, out_features=4, bias=True)
 ),
 1.574082612991333,
 {'Overall Survival (4 Years)': {'accuracy': 0.891156462585034,
   'mse': 0.1018331,
   'auc': 0.5276717557251909,
   'precision': 0.891156462585034,
   'recall': 1.0,
   'f1': 0.9424460431654677},
  'FT': {'accuracy': 0.7891156462585034,
   'mse': 0.15810017,
   'auc': 0.6880434782608696,
   'precision': 0.6666666666666666,
   'recall': 0.0625,
   'f1': 0.11428571428571428},
  'Aspiration rate Post-therapy': {'accuracy': 0.8095238095238095,
   'mse': 0.12137875,
   'auc': 0.8130959

In [167]:
train_state(model_args=t1_args,state=3,lr=.001,weights=[1,1,1,1],use_smote=True)

here
epoch 0 train loss 2.898747444152832
val loss 2.7859673500061035
______________
epoch 1 train loss 2.8460683822631836
val loss 2.7346413135528564
______________
epoch 2 train loss 2.8028929233551025
val loss 2.6850833892822266
______________
epoch 3 train loss 2.744980812072754


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


val loss 2.637294054031372
______________
epoch 4 train loss 2.6950490474700928
val loss 2.591198444366455
______________
epoch 5 train loss 2.6503114700317383
val loss 2.546651840209961
______________
epoch 6 train loss 2.6041817665100098
val loss 2.503596067428589
______________
epoch 7 train loss 2.5605216026306152
val loss 2.4620039463043213
______________
epoch 8 train loss 2.524507999420166
val loss 2.421823740005493
______________
epoch 9 train loss 2.4847936630249023
val loss 2.3829426765441895
______________
epoch 10 train loss 2.4436631202697754
val loss 2.3452610969543457
______________
epoch 11 train loss 2.3994269371032715
val loss 2.308797836303711
______________
epoch 12 train loss 2.3616127967834473
val loss 2.2734224796295166
______________
epoch 13 train loss 2.3210842609405518
val loss 2.239098310470581
______________
epoch 14 train loss 2.288273811340332
val loss 2.205782175064087
______________
epoch 15 train loss 2.260986566543579
val loss 2.1734306812286377
_____

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

val loss 2.142091751098633
______________
epoch 17 train loss 2.1931846141815186
val loss 2.1117067337036133
______________
epoch 18 train loss 2.150178909301758
val loss 2.0823583602905273
______________
epoch 19 train loss 2.120452404022217
val loss 2.053952693939209
______________
epoch 20 train loss 2.0926945209503174
val loss 2.026611804962158
______________
epoch 21 train loss 2.055915594100952
val loss 2.0003502368927
______________
epoch 22 train loss 2.0309133529663086
val loss 1.975046157836914
______________
epoch 23 train loss 1.9967169761657715
val loss 1.9507426023483276
______________
epoch 24 train loss 1.9829097986221313
val loss 1.9274749755859375
______________
epoch 25 train loss 1.9501252174377441
val loss 1.905211091041565
______________
epoch 26 train loss 1.929323673248291
val loss 1.8839943408966064
______________
epoch 27 train loss 1.903254747390747
val loss 1.8638575077056885
______________
epoch 28 train loss 1.8773410320281982
val loss 1.8448357582092285
_

...

val loss 1.6898722648620605
______________
epoch 42 train loss 1.6263933181762695
val loss 1.6841830015182495
______________
epoch 43 train loss 1.6118119955062866
val loss 1.6793715953826904
______________
epoch 44 train loss 1.5968177318572998
val loss 1.6752127408981323
______________
epoch 45 train loss 1.5824238061904907
val loss 1.6715989112854004
______________
epoch 46 train loss 1.5716044902801514
val loss 1.6684978008270264
______________
epoch 47 train loss 1.5595914125442505
val loss 1.6659307479858398
______________
epoch 48 train loss 1.5507481098175049
val loss 1.6637942790985107
______________
epoch 49 train loss 1.5342719554901123
val loss 1.6621489524841309
______________
epoch 50 train loss 1.5292648077011108
val loss 1.6609331369400024
______________
epoch 51 train loss 1.5241223573684692
val loss 1.6601277589797974
______________
epoch 52 train loss 1.5097386837005615
val loss 1.6596746444702148
______________
epoch 53 train loss 1.4989126920700073
val loss 1.65955

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

epoch 54 train loss 1.4968249797821045
val loss 1.6596627235412598
______________
epoch 55 train loss 1.480416178703308
val loss 1.6600149869918823
______________
epoch 56 train loss 1.471146821975708
val loss 1.6605663299560547
______________
epoch 57 train loss 1.4738041162490845
val loss 1.6613051891326904
______________
epoch 58 train loss 1.459065318107605
val loss 1.662140130996704
______________
epoch 59 train loss 1.4475079774856567
val loss 1.6630994081497192
______________
epoch 60 train loss 1.431553602218628
val loss 1.664210319519043
______________
epoch 61 train loss 1.4344451427459717
val loss 1.6652815341949463
______________
epoch 62 train loss 1.4291839599609375
val loss 1.6664941310882568
______________
epoch 63 train loss 1.4145889282226562
val loss 1.667707085609436
______________
epoch 64 train loss 1.4156335592269897
val loss 1.6688766479492188
______________
best loss 1.6595591306686401 {'Overall Survival (4 Years)': {'accuracy': 0.891156462585034, 'mse': 0.1067

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


(EndpointSimulator(
   (input_dropout): Dropout(p=0.1, inplace=False)
   (layers): ModuleList(
     (0): Linear(in_features=76, out_features=100, bias=True)
     (1): ReLU()
   )
   (batchnorm): BatchNorm1d(100, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
   (dropout): Dropout(p=0.1, inplace=False)
   (relu): Softplus(beta=1, threshold=20)
   (sigmoid): Sigmoid()
   (softmax): LogSoftmax(dim=1)
   (outcome_layer): Linear(in_features=100, out_features=4, bias=True)
 ),
 1.6595591306686401,
 {'Overall Survival (4 Years)': {'accuracy': 0.891156462585034,
   'mse': 0.10674424,
   'auc': 0.521469465648855,
   'precision': 0.891156462585034,
   'recall': 1.0,
   'f1': 0.9424460431654677},
  'FT': {'accuracy': 0.782312925170068,
   'mse': 0.16019534,
   'auc': 0.7119565217391304,
   'precision': 0.0,
   'recall': 0.0,
   'f1': 0.0},
  'Aspiration rate Post-therapy': {'accuracy': 0.8231292517006803,
   'mse': 0.12923922,
   'auc': 0.733630006357279,
   'precision': 0.0,
   

In [168]:
def train_model_ensemble(model_arg_list,state,
                         n_bags=20,
                         smote_options=[True,False],
                         smote_baseline_options=[True,False],
                         weight_options=[None],
                         weight_baseline_options=[None],
                         **kwargs):
    resampled_models =[]
    base_models = []
    base_metrics = []
    resample_metrics = []
    base_losses = []
    resample_losses = []
    n_errors = 0
    for margs in model_arg_list:
        for s in smote_baseline_options:
            for w in weight_baseline_options:
                [base_model,blosses,bmetrics] = train_state(model_args=margs,state=state,
                                         resample_training=False,
                                         use_smote=smote_options,
                                         weights=w,
                                         verbose=False,**kwargs)
                base_models.append(base_model)
                base_metrics.append(bmetrics)
                base_losses.append(blosses)
        for n in range(n_bags):
            for s in smote_options:
                for w in weight_options:
                    #this can fail if I resample a bad distribution with no minority classes
                    done = False
                    while not done:
                        try:
                            [model,loss,metrics] = train_state(model_args=margs,
                                                state=state,resample_training=True,
                                                use_smote=s,
                                                weights=w,
                                                verbose=False,**kwargs)
                            resampled_models.append(model)
                            resample_metrics.append(metrics)
                            resample_losses.append(loss)
                            done=True
                            print('model_done',len(base_models)+len(resampled_models))
                        except Exception as e:
                            print('error training model')
                            print(e)
                            n_errors += 1
    print('done with',n_errors,'errors')
    return base_models,resampled_models


In [172]:
t1_arglist = [
     {'hidden_layers': [400,400], 'dropout': 0.5, 'input_dropout': 0.25},
     {'hidden_layers': [10,10], 'dropout': 0.1, 'input_dropout': .1},
]
m1_list, m1_ensemble = train_model_ensemble(t1_arglist,1,
                                            n_bags=10,
                                           )
from Models import *
emodel1 = TransitionEnsemble(m1_list,m1_ensemble)
test2 = emodel1(transition_sample(1)[0][0].view(1,-1).to(emodel1.get_device()))
test2

here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.9354206323623657 {'pd': {'accuracy': 0.4723809523809524, 'auc_micro': 0.7912946428571429, 'auc_mean': 0.6129767194107202, 'auc_weighted': 0.6771378301898325}, 'nd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.861598440545809, 'auc_mean': 0.4527800865764336, 'auc_weighted': 0.48749641634861757}, 'mod': {'accuracy': 0.3333333333333333, 'auc_micro': 0.861598440545809, 'auc_mean': 0.4527800865764336, 'auc_weighted': 0.48749641634861757}, 'dlts': {'accuracy': [0.7857142857142857, 0.9464285714285714, 1.0, 0.9107142857142857, 1.0, 0.8928571428571429, 0.8035714285714286, 1.0], 'accuracy_mean': 0.8678571428571429, 'auc': [0.4772727272727273, 0.45911949685534587, -1, 0.592156862745098, -1, 0.5266666666666667, 0.5696969696969697, -1], 'auc_mean': 0.5249825446473616}}
here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.9200057983398438 {'pd': {'accuracy': 0.4338095238095238, 'auc_micro': 0.7943239795918368, 'auc_mean': 0.6203764338766193, 'auc_weighted': 0.6738806243811805}, 'nd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8656595191682912, 'auc_mean': 0.4792501701713527, 'auc_weighted': 0.5241974860685552}, 'mod': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8656595191682912, 'auc_mean': 0.4792501701713527, 'auc_weighted': 0.5241974860685552}, 'dlts': {'accuracy': [0.7857142857142857, 0.9464285714285714, 1.0, 0.9107142857142857, 1.0, 0.8928571428571429, 0.8035714285714286, 1.0], 'accuracy_mean': 0.8678571428571429, 'auc': [0.44886363636363635, 0.440251572327044, -1, 0.615686274509804, -1, 0.3933333333333333, 0.5838383838383838, -1], 'auc_mean': 0.4963946400744403}}
here


...

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 2.1053829193115234 {'pd': {'accuracy': 0.41768707482993195, 'auc_micro': 0.772214197828064, 'auc_mean': 0.5295522660920614, 'auc_weighted': 0.6214275160852035}, 'nd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8582796513830996, 'auc_mean': 0.3901491131329841, 'auc_weighted': 0.3641517980227658}, 'mod': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8582796513830996, 'auc_mean': 0.3901491131329841, 'auc_weighted': 0.3641517980227658}, 'dlts': {'accuracy': [0.7959183673469388, 0.9489795918367347, 0.9693877551020408, 0.9387755102040817, 1.0, 0.8775510204081632, 0.8367346938775511, 0.9693877551020408], 'accuracy_mean': 0.9052478134110787, 'auc': [0.5955128205128205, 0.3053763440860215, 0.775438596491228, 0.592391304347826, -1, 0.44089147286821706, 0.6646341463414634, 0.4982456140350877], 'auc_mean': 0.5532128998118092}}
model_done 41
best loss 2.1877877712249756 {'pd': {'accuracy': 0.3277777777777778, 'auc_micro': 0.6984900855011824, 'auc_mean': 0.4723151390833556, 'auc_wei

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 2.5386812686920166 {'pd': {'accuracy': 0.3863888888888889, 'auc_micro': 0.742767447476455, 'auc_mean': 0.4966325145305673, 'auc_weighted': 0.5632298625051508}, 'nd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8512174888986483, 'auc_mean': 0.3765338970686385, 'auc_weighted': 0.37535376676270144}, 'mod': {'accuracy': 0.3333333333333333, 'auc_micro': 0.8512174888986483, 'auc_mean': 0.3765338970686385, 'auc_weighted': 0.37535376676270144}, 'dlts': {'accuracy': [0.8431372549019608, 0.9509803921568627, 0.00980392156862745, 0.8823529411764706, 0.9509803921568627, 0.8627450980392157, 0.803921568627451, 1.0], 'accuracy_mean': 0.757703081232493, 'auc': [0.6351744186046512, 0.2515463917525773, -1, 0.5185185185185185, -1, 0.46266233766233766, 0.5908536585365853, -1], 'auc_mean': 0.491751065014934}}
model_done 43
best loss 1.9923418760299683 {'pd': {'accuracy': 0.4095860566448802, 'auc_micro': 0.7868751104045222, 'auc_mean': 0.5831162061832802, 'auc_weighted': 0.6491575375089307}, 'n

{'predictions': [tensor([[0.1081, 0.8786, 0.0133]], device='cuda:0', grad_fn=<MeanBackward1>),
  tensor([[0.0725, 0.8835, 0.0439]], device='cuda:0', grad_fn=<MeanBackward1>),
  tensor([[0.7677, 0.0363, 0.0350, 0.0374, 0.0344, 0.0536, 0.0356]],
         device='cuda:0', grad_fn=<MeanBackward1>),
  tensor([[0.0489, 0.0299, 0.0269, 0.0550, 0.0281, 0.1051, 0.0701, 0.0180]],
         device='cuda:0', grad_fn=<MeanBackward1>)],
 '5%': [tensor([[0.0778, 0.4776, 0.0095]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.0340, 0.6415, 0.0231]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.2136, 0.0234, 0.0189, 0.0311, 0.0188, 0.0429, 0.0180]],
         device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.0441, 0.0129, 0.0187, 0.0420, 0.0154, 0.0725, 0.0478, 0.0098]],
         device='cuda:0', grad_fn=<ViewBackward0>)],
 '95%': [tensor([[0.3619, 0.9062, 0.1977]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.2157, 0.9436, 0.1847]], device='cuda:0', grad_fn=<ViewBac

In [173]:
t2_arglist = [
    {'hidden_layers': [400], 'dropout': .9, 'input_dropout': .5},
     {'hidden_layers': [100], 'dropout': 0.9, 'input_dropout': 0.5},
]
m2_list, m2_ensemble = train_model_ensemble(t2_arglist,2,
                                            n_bags=10)
emodel2 = TransitionEnsemble(m2_list,m2_ensemble)
emodel2(transition_sample(2)[0][0].view(1,-1))

here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.4185909032821655 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.9348110736999626, 'auc_mean': 0.6766607634255394, 'auc_weighted': 0.709309652416485}, 'nd': {'accuracy': 0.34884777669587796, 'auc_micro': 0.735453251067869, 'auc_mean': 0.588782398721423, 'auc_weighted': 0.5075064363143631}, 'mod': {'accuracy': 0.34884777669587796, 'auc_micro': 0.735453251067869, 'auc_mean': 0.588782398721423, 'auc_weighted': 0.5075064363143631}, 'dlts': {'accuracy': [0.9523809523809523, 0.9795918367346939, 1.0, 0.9659863945578231, 1.0, 0.9659863945578231, 0.9183673469387755, 1.0], 'accuracy_mean': 0.9564625850340136, 'auc': [0.6581632653061225, 0.4027777777777778, -1, 0.4563380281690141, -1, 0.647887323943662, 0.7314814814814815, -1], 'auc_mean': 0.5793295753356115}}
here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.4045778512954712 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.9381780770669659, 'auc_mean': 0.703374569191377, 'auc_weighted': 0.7270863883010975}, 'nd': {'accuracy': 0.332878935410581, 'auc_micro': 0.7373991457047936, 'auc_mean': 0.5905943529520764, 'auc_weighted': 0.5176783778552072}, 'mod': {'accuracy': 0.332878935410581, 'auc_micro': 0.7373991457047936, 'auc_mean': 0.5905943529520764, 'auc_weighted': 0.5176783778552072}, 'dlts': {'accuracy': [0.9523809523809523, 0.9795918367346939, 1.0, 0.9659863945578231, 1.0, 0.9659863945578231, 0.9183673469387755, 1.0], 'accuracy_mean': 0.9564625850340136, 'auc': [0.6755102040816326, 0.40509259259259256, -1, 0.4859154929577465, -1, 0.5507042253521126, 0.7407407407407407, -1], 'auc_mean': 0.571592651144965}}
here


...

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.6040623188018799 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.9081797068595749, 'auc_mean': 0.6214650538030191, 'auc_weighted': 0.6496674621786297}, 'nd': {'accuracy': 0.34375, 'auc_micro': 0.7320968834688347, 'auc_mean': 0.5679280324287959, 'auc_weighted': 0.5184063591103897}, 'mod': {'accuracy': 0.34375, 'auc_micro': 0.7320968834688347, 'auc_mean': 0.5679280324287959, 'auc_weighted': 0.5184063591103897}, 'dlts': {'accuracy': [0.9534883720930233, 0.9767441860465116, 1.0, 0.9534883720930233, 1.0, 0.9700996677740864, 0.9501661129568106, 0.9867109634551495], 'accuracy_mean': 0.9651162790697675, 'auc': [0.6177202588352415, 0.67444120505345, -1, 0.6503235440517671, -1, 0.7667427701674276, 0.5377622377622377, 0.6843434343434344], 'auc_mean': 0.6552222417022596}}
model_done 41
best loss 1.4324604272842407 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.9350948739048356, 'auc_mean': 0.6949074143294869, 'auc_weighted': 0.6443805361640189}, 'nd': {'accuracy': 0.3261

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.4464795589447021 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.9310731839467471, 'auc_mean': 0.635571518362216, 'auc_weighted': 0.6160050093383427}, 'nd': {'accuracy': 0.3424564270152506, 'auc_micro': 0.745162486515642, 'auc_mean': 0.5803998565533688, 'auc_weighted': 0.5395619055220477}, 'mod': {'accuracy': 0.3424564270152506, 'auc_micro': 0.745162486515642, 'auc_mean': 0.5803998565533688, 'auc_weighted': 0.5395619055220477}, 'dlts': {'accuracy': [0.9536423841059603, 0.9768211920529801, 1.0, 0.9668874172185431, 0.9966887417218543, 0.9768211920529801, 0.9437086092715232, 0.9900662251655629], 'accuracy_mean': 0.9720908230842006, 'auc': [0.6604662698412699, 0.5230024213075061, -1, 0.601027397260274, -1, 0.6227602905569007, 0.7318885448916408, 0.8283166109253066], 'auc_mean': 0.661243589130483}}
model_done 43
best loss 1.4585955142974854 {'pd': {'accuracy': 0.3333333333333333, 'auc_micro': 0.9429753927586012, 'auc_mean': 0.6340823252825051, 'auc_weighted': 0.6804127471

{'predictions': [tensor([[0.7181, 0.2625, 0.0193]], device='cuda:0', grad_fn=<MeanBackward1>),
  tensor([[0.4419, 0.5265, 0.0316]], device='cuda:0', grad_fn=<MeanBackward1>),
  tensor([[0.0848, 0.6779, 0.1804, 0.0570]], device='cuda:0',
         grad_fn=<MeanBackward1>),
  tensor([[0.0655, 0.0314, 0.0042, 0.0671, 0.0042, 0.0257, 0.0615, 0.0280]],
         device='cuda:0', grad_fn=<MeanBackward1>)],
 '5%': [tensor([[0.6337, 0.1332, 0.0146]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.3575, 0.4374, 0.0190]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.0717, 0.5239, 0.1288, 0.0508]], device='cuda:0',
         grad_fn=<ViewBackward0>),
  tensor([[0.0431, 0.0189, 0.0024, 0.0311, 0.0030, 0.0171, 0.0333, 0.0146]],
         device='cuda:0', grad_fn=<ViewBackward0>)],
 '95%': [tensor([[0.8407, 0.3332, 0.0931]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.5227, 0.6077, 0.0778]], device='cuda:0', grad_fn=<ViewBackward0>),
  tensor([[0.1598, 0.7391, 0.2445, 0.0

In [175]:
t3_arglist = [
     {'hidden_layers': [10,10], 'dropout': 0.1, 'input_dropout': .1},
    {'hidden_layers': [100], 'dropout': 0.5, 'input_dropout': 0.1},
]
m3_list, m3_ensemble = train_model_ensemble(t3_arglist,3,n_bags=10,
                                           )
emodel3 = EndpointEnsemble(m3_list,m3_ensemble)
emodel3(transition_sample(3)[0][0].view(1,-1))

here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

best loss 1.6287031173706055 {'Overall Survival (4 Years)': {'accuracy': 0.891156462585034, 'mse': 0.10747933, 'auc': 0.5171755725190839, 'precision': 0.891156462585034, 'recall': 1.0, 'f1': 0.9424460431654677}, 'FT': {'accuracy': 0.7891156462585034, 'mse': 0.15839861, 'auc': 0.7244565217391304, 'precision': 0.6666666666666666, 'recall': 0.0625, 'f1': 0.11428571428571428}, 'Aspiration rate Post-therapy': {'accuracy': 0.8231292517006803, 'mse': 0.12356539, 'auc': 0.8048315321042594, 'precision': 0.0, 'recall': 0.0, 'f1': 0.0}, 'LRC': {'accuracy': 0.891156462585034, 'mse': 0.114108816, 'auc': 0.6934343434343435, 'precision': 0.9084507042253521, 'recall': 0.9772727272727273, 'f1': 0.9416058394160584}}
here


...

best loss 1.6915063858032227 {'Overall Survival (4 Years)': {'accuracy': 0.8678571428571429, 'mse': 0.11696893, 'auc': 0.5555555555555556, 'precision': 0.8678571428571429, 'recall': 1.0, 'f1': 0.9292543021032504}, 'FT': {'accuracy': 0.8285714285714286, 'mse': 0.134682, 'auc': 0.677801724137931, 'precision': 0.5, 'recall': 0.020833333333333332, 'f1': 0.039999999999999994}, 'Aspiration rate Post-therapy': {'accuracy': 0.8071428571428572, 'mse': 0.13643225, 'auc': 0.7518846279908227, 'precision': 0.0, 'recall': 0.0, 'f1': 0.0}, 'LRC': {'accuracy': 0.8821428571428571, 'mse': 0.103058405, 'auc': 0.6486320696847012, 'precision': 0.8821428571428571, 'recall': 1.0, 'f1': 0.937381404174573}}
model_done 42
here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


best loss 1.8912644386291504 {'Overall Survival (4 Years)': {'accuracy': 0.856655290102389, 'mse': 0.12198683, 'auc': 0.6103206222728136, 'precision': 0.856655290102389, 'recall': 1.0, 'f1': 0.9227941176470588}, 'FT': {'accuracy': 0.7781569965870307, 'mse': 0.16865371, 'auc': 0.6363697705802969, 'precision': 0.0, 'recall': 0.0, 'f1': 0.0}, 'Aspiration rate Post-therapy': {'accuracy': 0.8156996587030717, 'mse': 0.14243874, 'auc': 0.6837904850457152, 'precision': 0.0, 'recall': 0.0, 'f1': 0.0}, 'LRC': {'accuracy': 0.8600682593856656, 'mse': 0.120950796, 'auc': 0.6127564847077043, 'precision': 0.8600682593856656, 'recall': 1.0, 'f1': 0.9247706422018349}}
model_done 43
best loss 1.591996192932129 {'Overall Survival (4 Years)': {'accuracy': 0.8719723183391004, 'mse': 0.11877448, 'auc': 0.574109824109824, 'precision': 0.8719723183391004, 'recall': 1.0, 'f1': 0.9316081330868762}, 'FT': {'accuracy': 0.8200692041522492, 'mse': 0.13343531, 'auc': 0.7527974783293933, 'precision': 0.6, 'recall': 0

{'predictions': tensor([[0.7840, 0.1871, 0.2169, 0.8109]], device='cuda:0',
        grad_fn=<MeanBackward1>),
 '5%': tensor([[0.6247, 0.1698, 0.1853, 0.6962]], device='cuda:0',
        grad_fn=<ViewBackward0>),
 '95%': tensor([[0.8508, 0.4007, 0.3801, 0.8898]], device='cuda:0',
        grad_fn=<ViewBackward0>)}

In [ ]:
len(emodel3.base_models)

In [24]:
def gridsearch_attention_transition_models(state=1,attentions=[False]):
    hiddenlayers = [[10],[50],[100],[400],[1000,100],[10,10],[50,50],[100,100],[400,400]]
    model_arglist = [{'hidden_layers': h} for h in hiddenlayers]
    best_loss = 100000000000
    best_metrics = {}
    best_args = {}
    best_model = None
    k = 0
    records = []
    for margs in model_arglist:
        args = {k:v for k,v in margs.items()}
        for use_smote in [True,False]:
            for dropout in [0,.1,.25,.5,.9]:
                args['dropout'] = dropout
                for input_dropout in [0,.1,.25,.5]:
                    args['input_dropout'] = input_dropout
                    model,m_loss,m_metrics = train_state(
                        model_args=args,
                        state=state,
                        lr=.001,
                        use_smote=use_smote,
                        use_attention=False,
                        verbose=False)
                    newargs = {k:copy.deepcopy(v) for k,v in args.items()}
                    newargs['use_smote'] = use_smote
                    record = {'loss': m_loss,'metrics':m_metrics,'args':newargs,'model': model}
                    records.append(record)
                    print('done',k,m_loss)
                    k+=1
                    if m_loss < best_loss:
                        best_loss = m_loss
                        best_metrics  = m_metrics
                        best_model = model
                        best_args = {k:v for k,v in args.items()}
                        best_args['smote'] = use_smote
                        print('_++++++++++New Best++++____')
                        print(best_loss)
                        print(best_metrics)
                        print(best_args)
                        print(use_smote)
                        print('___________')
                        print('++++++++')
                        print()
    print('_________')
    print('+++++++++++')
    print('best stuff',best_loss)
    print(best_metrics)
    print(best_args)
    return best_model, records
# model1_gs = gridsearch_attention_transition_models(1)
# model1_gs[0]

In [25]:
# model2_gs = gridsearch_attention_transition_models(2)
# model2_gs[0]

In [26]:
# model3_gs= gridsearch_attention_transition_models(3)
# model3_gs[0]

here


/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.8314793109893799 {'Overall Survival (4 Years)': {'accuracy': 0.8571428571428571, 'mse': 0.1243038, 'auc': 0.4770992366412214, 'precision': 0.9104477611940298, 'recall': 0.9312977099236641, 'f1': 0.9207547169811321}, 'FT': {'accuracy': 0.7619047619047619, 'mse': 0.16614403, 'auc': 0.6635869565217392, 'precision': 0.4117647058823529, 'recall': 0.21875, 'f1': 0.2857142857142857}, 'Aspiration rate Post-therapy': {'accuracy': 0.8231292517006803, 'mse': 0.14100426, 'auc': 0.7946598855689765, 'precision': 0.5, 'recall': 0.46153846153846156, 'f1': 0.48000000000000004}, 'LRC': {'accuracy': 0.8639455782312925, 'mse': 0.12312649, 'auc': 0.47727272727272724, 'precision': 0.9, 'recall': 0.9545454545454546, 'f1': 0.9264705882352942}}
done 0 1.8314793109893799
_++++++++++New Best++++____
1.8314793109893799
{'Overall Survival (4 Years)': {'accuracy': 0.8571428571428571, 'mse': 0.1243038, 'auc': 0.4770992366412214, 'precision': 0.9104477611940298, 'recall': 0.9312977099236641, 'f1': 0.92075

/usr/local/lib/python3.8/dist-packages/imblearn/over_sampling/_smote/base.py:345: FutureWarning: The parameter `n_jobs` has been deprecated in 0.10 and will be removed in 0.12. You can pass an nearest neighbors estimator where `n_jobs` is already set instead.
  warnings.warn(


best loss 1.7722574472427368 {'Overall Survival (4 Years)': {'accuracy': 0.8571428571428571, 'mse': 0.12560907, 'auc': 0.46564885496183206, 'precision': 0.8985507246376812, 'recall': 0.9465648854961832, 'f1': 0.9219330855018587}, 'FT': {'accuracy': 0.7619047619047619, 'mse': 0.17506051, 'auc': 0.6516304347826086, 'precision': 0.4, 'recall': 0.1875, 'f1': 0.25531914893617025}, 'Aspiration rate Post-therapy': {'accuracy': 0.7891156462585034, 'mse': 0.13096674, 'auc': 0.7965670692943421, 'precision': 0.3684210526315789, 'recall': 0.2692307692307692, 'f1': 0.3111111111111111}, 'LRC': {'accuracy': 0.8843537414965986, 'mse': 0.11268359, 'auc': 0.6227272727272728, 'precision': 0.9078014184397163, 'recall': 0.9696969696969697, 'f1': 0.9377289377289377}}
done 1 1.7722574472427368
_++++++++++New Best++++____
1.7722574472427368
{'Overall Survival (4 Years)': {'accuracy': 0.8571428571428571, 'mse': 0.12560907, 'auc': 0.46564885496183206, 'precision': 0.8985507246376812, 'recall': 0.946564885496183

...

best loss 1.5873210430145264 {'Overall Survival (4 Years)': {'accuracy': 0.891156462585034, 'mse': 0.10515472, 'auc': 0.5658396946564885, 'precision': 0.891156462585034, 'recall': 1.0, 'f1': 0.9424460431654677}, 'FT': {'accuracy': 0.782312925170068, 'mse': 0.15795794, 'auc': 0.7114130434782608, 'precision': 0.5, 'recall': 0.09375, 'f1': 0.15789473684210525}, 'Aspiration rate Post-therapy': {'accuracy': 0.8095238095238095, 'mse': 0.12177198, 'auc': 0.8038779402415765, 'precision': 0.375, 'recall': 0.11538461538461539, 'f1': 0.1764705882352941}, 'LRC': {'accuracy': 0.8979591836734694, 'mse': 0.09483484, 'auc': 0.6292929292929292, 'precision': 0.8979591836734694, 'recall': 1.0, 'f1': 0.9462365591397849}}
done 358 1.5873210430145264


/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.8/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMe

best loss 1.5910322666168213 {'Overall Survival (4 Years)': {'accuracy': 0.891156462585034, 'mse': 0.11064984, 'auc': 0.5667938931297709, 'precision': 0.891156462585034, 'recall': 1.0, 'f1': 0.9424460431654677}, 'FT': {'accuracy': 0.7959183673469388, 'mse': 0.15551725, 'auc': 0.7182065217391305, 'precision': 0.6666666666666666, 'recall': 0.125, 'f1': 0.21052631578947367}, 'Aspiration rate Post-therapy': {'accuracy': 0.8027210884353742, 'mse': 0.12270794, 'auc': 0.8032422123331214, 'precision': 0.2, 'recall': 0.038461538461538464, 'f1': 0.06451612903225806}, 'LRC': {'accuracy': 0.8979591836734694, 'mse': 0.09806414, 'auc': 0.6540404040404041, 'precision': 0.8979591836734694, 'recall': 1.0, 'f1': 0.9462365591397849}}
done 359 1.5910322666168213
_________
+++++++++++
best stuff 1.539259672164917
{'Overall Survival (4 Years)': {'accuracy': 0.891156462585034, 'mse': 0.106308855, 'auc': 0.5596374045801527, 'precision': 0.891156462585034, 'recall': 1.0, 'f1': 0.9424460431654677}, 'FT': {'accu

EndpointSimulator(
  (input_dropout): Dropout(p=0.25, inplace=False)
  (layers): ModuleList(
    (0): Linear(in_features=76, out_features=50, bias=True)
    (1): ReLU()
    (2): Linear(in_features=50, out_features=50, bias=True)
    (3): ReLU()
  )
  (batchnorm): BatchNorm1d(50, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (dropout): Dropout(p=0.25, inplace=False)
  (relu): Softplus(beta=1, threshold=20)
  (sigmoid): Sigmoid()
  (softmax): LogSoftmax(dim=1)
  (outcome_layer): Linear(in_features=50, out_features=4, bias=True)
)

In [27]:
# [(m['args'],m['loss']) for m in sorted(model1_gs[1], key = lambda x: x['loss'])]

In [28]:
# [(m['args'],m['loss']) for m in sorted(model2_gs[1], key = lambda x: x['loss'])]

In [29]:
# [(m['args'],m['loss']) for m in sorted(model3_gs[1], key = lambda x: x['loss'])]

In [ ]:
# def load_trained_models():
#     files = Const.tuned_transition_models
#     decision_file = Const.tuned_decision_model
#     [model1,model2,model3] = [torch.load(file) for file in files]
#     decision_model = torch.load(decision_file)
#     return decision_model, model1,model2,model3
# _, model1, model2, model3 =load_trained_models()

In [35]:
def calc_optimal_decisions(dataset,ids,m1,m2,m3,weights=[-1,1,1,-1],outcome_loss_func=None,get_transitions=True):
    m1.eval()
    m2.eval()
    m3.eval()
    device = m1.get_device()
    data = dataset.processed_df.copy().loc[ids]
    
    def get_dlt(state):
        if state == 2:
            return data[Const.dlt2].copy()
        d = data[Const.dlt1].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_pd(state):
        if state == 2:
            return data[Const.primary_disease_states2].copy()
        d = data[Const.primary_disease_states].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_nd(state):
        if state == 2:
            return data[Const.nodal_disease_states2].copy()
        d = data[Const.nodal_disease_states].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_cc(state):
        res = data[Const.ccs].copy()
        if state == 1:
            res.values[:,:] = np.zeros(res.values.shape)
        return res
    
    def get_mod(state):
        res = data[Const.modifications].copy()
        #this should have an ic condition but we don't use it anumore anywa
        return res
        
    def formatdf(d):
        d = df_to_torch(d).to(device)
        return d
    
    
    outcomedf = data[Const.outcomes]
    baseline = dataset.get_state('baseline').loc[ids]
    baseline_input = formatdf(baseline)

    
    def outcome_loss(ypred):
        l = torch.mul((-1*(ypred[:,0] - 1)),-weights[0])
        for i,weight in enumerate(weights[1:]):
            #weights with negative values will invert the outcome so e.g. Regional control becomes no regional control
            #so the penaly is correct
            if weight > 0:
                newloss = torch.mul(ypred[:,i],weight)
            else:
                newloss = torch.mul(-1*(ypred[:,i] - 1),-weights[i])
            l = torch.add(l,newloss)
        return l
    if outcome_loss_func is None:
        outcome_loss_func = outcome_loss
    
    cat = lambda x: torch.cat([xx.to(device) for xx in x],axis=1).to(device)
    format_transition = lambda x: x.to(device)
    
    def get_outcome(d1,d2,d3):
        d1 = torch.full((len(ids),1),d1).type(torch.FloatTensor)
        d2 = torch.full((len(ids),1),d2).type(torch.FloatTensor)
        d3 = torch.full((len(ids),1),d3).type(torch.FloatTensor)
        
        tinput1 = cat([baseline_input,d1])
        ytransition = m1(tinput1)
        [ypd1,ynd1,ymod,ydlt1] = [format_transition(xx) for xx in ytransition['predictions']]
        d1_thresh = torch.gt(d1,.5).view(-1,1).to(device)
        ypd1[:,0:2] = ypd1[:,0:2]*d1_thresh
        ynd1[:,0:2] = ynd1[:,0:2]*d1_thresh
        
        tinput2 = cat([baseline_input,ypd1,ynd1,ymod,ydlt1,d1,d2])
        ytransition2 = m2(tinput2)
        [ypd2,ynd2,ycc,ydlt2] = [format_transition(xx) for xx in ytransition2['predictions']]
        
        input3 = cat([baseline_input, ypd2, ynd2, ycc, ydlt2, d1, d2,d3])
        outcome = m3(input3)['predictions']
        transitions = {
            'pd1': ypd1,
            'nd1': ynd1,
            'nd2': ynd2,
            'pd2': ypd2,
            'mod': ymod,
            'cc': ycc,
            'dlt1': ydlt1,
            'dlt2': ydlt2,
        }
        return outcome, transitions

    losses = []
    loss_order = []
    transitions = {}
    for d1 in [0,1]:
        for d2 in [0,1]:
            for d3 in [0,1]:
                outcomes, transition_entry = get_outcome(d1,d2,d3)
                loss = outcome_loss_func(outcomes)
                losses.append(loss)
                loss_order.append([d1,d2,d3])
                transitions[str(d1)+str(d2)+str(d3)] = transition_entry
    losses = torch.stack(losses,axis=1)
    optimal_decisions = [loss_order[i] for i in torch.argmin(losses,axis=1)]
    result = torch.tensor(optimal_decisions).type(torch.FloatTensor)
    if get_transitions:
        opt_transitions = {k: torch.zeros(v.shape).type(torch.FloatTensor) for k,v in transitions['000'].items()}
        for i,od in enumerate(optimal_decisions):
            key = ''.join([str(o) for o in od])
            entry = transitions[key]
            for kk,vv in entry.items():
                opt_transitions[kk][i,:] = vv[i,:]
        return result, opt_transitions
    return result

test, testtest = get_tt_split()
calc_optimal_decisions(DTDataset(),testtest,emodel1,emodel2,emodel3)

(tensor([[1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [0., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1., 0., 0.],
         [1

In [156]:
def torch_apply_along_axis(function, x, axis: int = 0):
    return torch.stack([
        function(x_i) for x_i in torch.unbind(x, dim=axis)
    ], dim=axis)

def get_unique_sequence(array):
    #converts a row of boolean values to a unique number e.g. [1,1,0] => 11, [0,0,1] => 100
    uniqueify = lambda r: torch.sum(torch.stack([i*(10**ii) for ii,i in enumerate(r)]))
    return torch_apply_along_axis(uniqueify,array)

def train_decision_model_triplet(
    tmodel1,
    tmodel2,
    tmodel3,
    use_default_split=True,
    use_bagging_split=False,
    lr=.001,
    epochs=10000,
    patience=5,
    weights=[-1,1,1,-1], #realtive weight of survival, feeding tube, aspiration, andl lrc
    opt_weights=[1,1,1],
    imitation_weights=[.5,1,1],#weights of imitation decisions, because ic overtrains too quickly
    imitation_weight=1,
    reward_weight=1,
    imitation_triplet_weight=2,
    reward_triplet_weight = 2,
    shufflecol_chance = 0.1,
    split=.7,
    resample_training=False,
    save_path='../data/models/',
    file_suffix='',
    verbose=True,
    use_gpu=False,
    validate_with_memory=True,
    **model_kwargs,
):
    tmodel1.eval()
    tmodel2.eval()
    tmodel3.eval()

    train_ids, test_ids = get_tt_split(use_default_split=use_default_split,use_bagging_split=use_bagging_split,resample_training=resample_training)
    true_ids = train_ids + test_ids #for saving memory without upsampling

    dataset = DTDataset()
    data = dataset.processed_df.copy()
    
    def get_dlt(state):
        if state == 2:
            return data[Const.dlt2].copy()
        d = data[Const.dlt1].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_pd(state):
        if state == 2:
            return data[Const.primary_disease_states2].copy()
        d = data[Const.primary_disease_states].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_nd(state):
        if state == 2:
            return data[Const.nodal_disease_states2].copy()
        d = data[Const.nodal_disease_states].copy()
        if state < 1:
            d.values[:,:] = 0
        return d
    
    def get_cc(state):
        res = data[Const.ccs].copy()
        if state == 1:
            res.values[:,:] = np.zeros(res.values.shape)
        return res
    
    def get_mod(state):
        res = data[Const.modifications].copy()
        #this should have an ic condition but we don't use it anumore anywa
        return res
        
    outcomedf = data[Const.outcomes]
    baseline = dataset.get_state('baseline')
    
    def formatdf(d,dids=train_ids):
        d = df_to_torch(d.loc[dids]).to(model.get_device())
        return d
    
    def makegrad(v):
        if not v.requires_grad:
            v.requires_grad=True
        return v
    
    model = DecisionModel(baseline.shape[1],**model_kwargs)

    device = 'cpu'
    if use_gpu and torch.cuda.is_available():
        device = 'cuda'
        
    model.set_device(device)

    tmodel1.set_device(device)
    tmodel2.set_device(device)
    tmodel3.set_device(device)
    hashcode = str(hash(','.join([str(i) for i in train_ids])))
    
    save_file = save_path + 'model_' + model.identifier +'_hash' + hashcode + file_suffix + '.tar'
    model.fit_normalizer(df_to_torch(baseline.loc[train_ids]))
    optimizer = torch.optim.Adam(model.parameters(),lr=lr)
    
    
    optimal_train,transitions_train = calc_optimal_decisions(dataset,train_ids,tmodel1,tmodel2,tmodel3,
                                           weights=weights,
                                          )
    optimal_test,transitions_test = calc_optimal_decisions(dataset,test_ids,tmodel1,tmodel2,tmodel3,
                                          weights=weights,
                                         )
    optimal_train = optimal_train.to(model.get_device())
    optimal_test = optimal_test.to(model.get_device())
    mse = torch.nn.MSELoss()
    nllloss = torch.nn.NLLLoss()
    bce = torch.nn.BCELoss()
    
    def compare_decisions(d1,d2,d3,ids):
#         ypred = np.concatenate([dd.cpu().detach().numpy().reshape(-1,1) for dd in [d1,d2,d3]],axis=1)
        ytrue = df_to_torch(outcomedf.loc[ids])
        dloss = bce(d1.view(-1),ytrue[:,0])
        dloss += bce(d2.view(-1),ytrue[:,1])
        dloss += bce(d3,view(-1),ytrue[:,2])
        return dloss
        
    def remove_decisions(df):
        cols = [c for c in df.columns if c not in Const.decisions ]
        ddf = df[cols]
        return ddf
    
    makeinput = lambda step,dids: df_to_torch(remove_decisions(dataset.get_input_state(step=step,ids=dids)))
    threshold = lambda x: torch.gt(x,torch.rand(x.shape[0])).type(torch.FloatTensor)

    randchoice = lambda x: x[torch.randint(len(x),(1,))[0]]
    tloss_func = torch.nn.TripletMarginLoss()
    def get_tloss(row,step,yt,x,imitation=True):
        if yt[:,step].std() < .001:
            return torch.tensor([0]).to(device)
        positive_idx= torch.nonzero(yt[:,step] == yt[row,step])
        positive_idx = torch.stack([ii for ii in positive_idx if ii != row]).view(-1)
        negative_idx = torch.tensor([ii for ii in range(x.shape[0]) if ii not in positive_idx and ii != row])
        if len(positive_idx) < 1 or len(negative_idx) < 1:
            print('no losses','n positive',len(positive_idx),'n negative',len(negative_idx),'yt',yt[row,step],'row',row,'step',step,'imitation',imitation,end='\r')
            return torch.tensor([0]).to(device)
        positive = x[randchoice(positive_idx)]
        negative = x[randchoice(negative_idx)]
        anchor = x[row]
        [anchor_embedding,pos_embedding,neg_embedding] = [model.get_embedding(xx.view(1,-1),position=step,concatenate=False)[int(imitation)] for xx in [anchor,positive,negative]]
        tloss = tloss_func(anchor_embedding,pos_embedding,neg_embedding)
        return tloss
        
    def step(train=True):
        if train:
            model.train(True)
            tmodel1.train(True)
            tmodel2.train(True)
            tmodel3.train(True)
            optimizer.zero_grad()
            ids = train_ids
            y_opt = makegrad(optimal_train)
            transition_dict = {k: torch.clone(v).detach() for k,v in transitions_train.items()}
        else:
            ids = test_ids
            model.eval()
            tmodel1.eval()
            tmodel2.eval()
            tmodel3.eval()
            y_opt = makegrad(optimal_test)
            transition_dict = {k: torch.clone(v).detach() for k,v in transitions_test.items()}
        model.set_device(device)
        ytrain = df_to_torch(outcomedf.loc[ids]).to(device)
        #imitation losses and decision 1
        xxtrained = [baseline, get_dlt(0),get_dlt(0),get_pd(0),get_nd(0),get_cc(0),get_mod(0)]
        xxtrain = [formatdf(xx,ids) for xx in xxtrained]
        xxtrain = torch.cat(xxtrain,axis=1).to(device)
        o1 = model(xxtrain,position=0)
        decision1_imitation = o1[:,3]
        decision1_opt = o1[:,0]
    
        imitation_loss1 = bce(decision1_imitation,ytrain[:,0])
        imitation_loss1 = torch.mul(imitation_loss1,imitation_weights[0])
        opt_loss1 = bce(decision1_opt,y_opt[:,0])
        opt_loss1 = torch.mul(opt_loss1,opt_weights[0])
        
        x1_imitation = [baseline, get_dlt(1),get_dlt(0),get_pd(1),get_nd(1),get_cc(1),get_mod(1)]
        x1_imitation = [formatdf(xx1,ids) for xx1 in x1_imitation]
        x1_imitation = torch.cat(x1_imitation,axis=1).to(device)
        
        o2 = model(x1_imitation,position=1)
            
        decision2_imitation = o2[:,4]
            
        imitation_loss2 =  bce(decision2_imitation,ytrain[:,1])
        imitation_loss2 = torch.mul(imitation_loss2,imitation_weights[1])
        
        
        x2_imitation = [baseline, get_dlt(1),get_dlt(2),get_pd(2),get_nd(2),get_cc(2),get_mod(2)]
        
        x2_imitation = [formatdf(xx2,ids) for xx2 in x2_imitation]
        x2_imitation = torch.cat(x2_imitation,axis=1).to(device)
        
        
        o3 = model(x2_imitation,position=2)
            
        decision3_imitation = o3[:,5]
        
        imitation_loss3 = bce(decision3_imitation,ytrain[:,2])
        imitation_loss3 = torch.mul(imitation_loss3,imitation_weights[2])
        
        opt_input2 = [
            formatdf(baseline,ids), 
            transition_dict['dlt1'],
            formatdf(get_dlt(0),ids),
            transition_dict['pd1'],
            transition_dict['nd1'], 
            formatdf(get_cc(0),ids),
            transition_dict['mod']
                 ]
        opt_input2 = [o.to(device) for o in opt_input2]

        opt_input2 = torch.cat(opt_input2,axis=1).to(device)
        decision2_opt = model(opt_input2,position=1)[:,1]
        
        opt_loss2 = bce(decision2_opt,y_opt[:,1])
        opt_loss2 = torch.mul(opt_loss2,opt_weights[1])
        
        opt_input3 = [
            formatdf(baseline,ids),
            transition_dict['dlt1'],
            transition_dict['dlt2'],
            transition_dict['pd2'],
            transition_dict['nd2'],
            transition_dict['cc'],
            transition_dict['mod'],
        ]
        opt_input3 = [o.to(device) for o in opt_input3]
        opt_input3 = torch.cat(opt_input3,axis=1).to(device)
        decision3_opt = model(opt_input3,position=2)[:,2]
        
        opt_loss3 = bce(decision3_opt,y_opt[:,2])
        opt_loss3 = torch.mul(opt_loss3,opt_weights[2])
        
        iloss = torch.add(torch.add(imitation_loss1,imitation_loss2),imitation_loss3)
        iloss = torch.mul(iloss,imitation_weight)
        
        reward_loss = torch.add(torch.add(opt_loss1,opt_loss2),opt_loss3)
        reward_loss =torch.mul(reward_loss,reward_weight)
        
        loss = torch.add(iloss,reward_loss)
        
        imitation_tloss = torch.FloatTensor([0]).to(device)
        opt_tloss = torch.FloatTensor([0]).to(device)
        n_rows = xxtrain.shape[0]
        if reward_triplet_weight + imitation_triplet_weight > 0.0001:
            for i in range(n_rows):
                
                if imitation_triplet_weight > .0001:
                    imitation_tloss += get_tloss(i,0,ytrain,xxtrain,True)
                    imitation_tloss += get_tloss(i,1,ytrain,x1_imitation,True)
                    imitation_tloss += get_tloss(i,2,ytrain,x2_imitation,True)
                if reward_triplet_weight > .0001:
                    opt_tloss += get_tloss(i,0,y_opt,xxtrain,False)
                    opt_tloss += get_tloss(i,1,y_opt,opt_input2,False)
                    opt_tloss += get_tloss(i,2,y_opt,opt_input3,False)
            loss += torch.mul(imitation_tloss[0],imitation_triplet_weight/n_rows)
            loss += torch.mul(opt_tloss[0],reward_triplet_weight/n_rows)
        losses = [iloss,reward_loss,imitation_tloss*imitation_triplet_weight/n_rows,opt_tloss*reward_triplet_weight/n_rows]
        
        if train:
            loss.backward()
            optimizer.step()
            return losses
        else:
            scores = []
            distributions = [decision1_opt.mean().item(),decision2_opt.mean().item(),decision3_opt.mean().item()]
            imitation = [decision1_imitation,decision2_imitation,decision3_imitation]
            optimal = [decision1_opt,decision2_opt,decision3_opt]
            for i,decision_im in enumerate(imitation):
                deci = decision_im.cpu().detach().numpy()
                deci0 = (deci > .5).astype(int)
                iout = ytrain[:,i].cpu().detach().numpy()
                acci = accuracy_score(iout,deci0)
                try:
                    auci = roc_auc_score(iout,deci)
                except:
                    auci = -1
                
                deco = optimal[i].cpu().detach().numpy()
                deci0 = (deco > .5).astype(int)
                oout = y_opt[:,i].cpu().detach().numpy()
                acco = accuracy_score(oout,deci0)
                try:
                    auco = roc_auc_score(oout,deco)
                except:
                    auco=-1
                scores.append({'decision': i,'optimal_auc': auco,'imitation_auc': auci,'optimal_acc': acco,'imitation_acc': acci})
            return losses, scores, distributions
        
    best_val_loss = torch.tensor(1000000000.0)
    steps_since_improvement = 0
    best_val_score = {}
    
    for epoch in range(epochs):
        losses = step(True)
        val_losses,val_metrics,val_distributions = step(False)
        vl = val_losses[0] + val_losses[1]
        for vm in val_metrics:
            vl += (-((vm['optimal_auc']*reward_weight) + (vm['imitation_auc']*imitation_weight)))/10
        if verbose:
            print('______epoch',str(epoch),'_____')
            print('val reward',val_losses[1].item())
            print('imitation reward', val_losses[0].item())
            print('distance losses',val_losses[2].item(),val_losses[-1].item())
            print('distributions',val_distributions)
            print(val_metrics)
        if vl < best_val_loss:
            best_val_loss = vl
            best_val_score = val_metrics
            best_val_distributions = val_distributions
            steps_since_improvement = 0
            torch.save(model.state_dict(),save_file)
        else:
            steps_since_improvement += 1
        if steps_since_improvement > patience:
            break
    print('++++++++++Final+++++++++++')
    print('best',best_val_loss)
    print(best_val_score)
    model.load_state_dict(torch.load(save_file))
    model.eval()
    return model, best_val_score, best_val_loss, best_val_distributions

from Models import *
args = {
    'hidden_layers': [500], 
    'opt_layer_size': 20, 
    'imitation_layer_size': 20, 
    'dropout': 0.25, 
    'input_dropout': 0.25, 
    'shufflecol_chance': 0.5
}

#1.8424
decision_model, decision_score, decision_loss, _ = train_decision_model_triplet(
    emodel1,emodel2,emodel3,
    lr=.001,
    imitation_weight=1,
    reward_weight=1,
    patience=10,
    verbose=True,
    **args)
decision_model

______epoch 0 _____
val reward 2.124905586242676
imitation reward 1.7047059535980225
distance losses 5.302173614501953 3.044980764389038
distributions [0.4675922095775604, 0.508781909942627, 0.49096253514289856]
[{'decision': 0, 'optimal_auc': 0.8649809160305344, 'imitation_auc': 0.6631679389312978, 'optimal_acc': 0.14285714285714285, 'imitation_acc': 0.48299319727891155}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.5809782608695652, 'optimal_acc': 0.2857142857142857, 'imitation_acc': 0.7891156462585034}, {'decision': 2, 'optimal_auc': 0.4334532374100719, 'imitation_auc': 0.4132231404958678, 'optimal_acc': 0.673469387755102, 'imitation_acc': 0.2108843537414966}]
______epoch 1 _____
val reward 2.058022975921631
imitation reward 1.6753144264221191
distance losses 5.1243391036987305 2.4738287925720215
distributions [0.4791638255119324, 0.49547290802001953, 0.4775824546813965]
[{'decision': 0, 'optimal_auc': 0.8520992366412213, 'imitation_auc': 0.6583969465648856, 'optimal_acc': 

______epoch 13 _____
val reward 1.350662112236023
imitation reward 1.3780319690704346
distance losses 4.927570819854736 1.7000536918640137
distributions [0.6189239025115967, 0.31713756918907166, 0.30941352248191833]
[{'decision': 0, 'optimal_auc': 0.3893129770992366, 'imitation_auc': 0.3945610687022901, 'optimal_acc': 0.891156462585034, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.7190217391304348, 'optimal_acc': 1.0, 'imitation_acc': 0.782312925170068}, {'decision': 2, 'optimal_auc': 0.2994604316546763, 'imitation_auc': 0.4570883661792753, 'optimal_acc': 0.9455782312925171, 'imitation_acc': 0.8231292517006803}]
______epoch 14 _____
val reward 1.299244999885559
imitation reward 1.3562147617340088
distance losses 5.114436149597168 1.3627454042434692
distributions [0.6311554908752441, 0.30202430486679077, 0.29543986916542053]
[{'decision': 0, 'optimal_auc': 0.3845419847328244, 'imitation_auc': 0.3812022900763359, 'optimal_acc': 0.891156462585

______epoch 26 _____
val reward 0.7828273773193359
imitation reward 1.1683058738708496
distance losses 5.560473918914795 1.0604134798049927
distributions [0.7768359780311584, 0.13076426088809967, 0.14333057403564453]
[{'decision': 0, 'optimal_auc': 0.5248091603053435, 'imitation_auc': 0.3606870229007634, 'optimal_acc': 0.891156462585034, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.7334239130434783, 'optimal_acc': 1.0, 'imitation_acc': 0.782312925170068}, {'decision': 2, 'optimal_auc': 0.6205035971223022, 'imitation_auc': 0.5429116338207247, 'optimal_acc': 0.9455782312925171, 'imitation_acc': 0.8231292517006803}]
______epoch 27 _____
val reward 0.753146767616272
imitation reward 1.1607118844985962
distance losses 5.344418525695801 1.3912874460220337
distributions [0.7872403264045715, 0.1200002059340477, 0.13366569578647614]
[{'decision': 0, 'optimal_auc': 0.5424618320610687, 'imitation_auc': 0.36736641221374045, 'optimal_acc': 0.89115646258

______epoch 39 _____
val reward 0.5459592342376709
imitation reward 1.1193861961364746
distance losses 5.16135311126709 1.3682736158370972
distributions [0.8659063577651978, 0.04700569435954094, 0.06908319145441055]
[{'decision': 0, 'optimal_auc': 0.7080152671755725, 'imitation_auc': 0.47328244274809156, 'optimal_acc': 0.891156462585034, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.7423913043478261, 'optimal_acc': 1.0, 'imitation_acc': 0.782312925170068}, {'decision': 2, 'optimal_auc': 0.866906474820144, 'imitation_auc': 0.6916719643992372, 'optimal_acc': 0.9455782312925171, 'imitation_acc': 0.8231292517006803}]
______epoch 40 _____
val reward 0.5373167991638184
imitation reward 1.1177324056625366
distance losses 5.3360724449157715 1.1555922031402588
distributions [0.8688344955444336, 0.04428356885910034, 0.06710859388113022]
[{'decision': 0, 'optimal_auc': 0.7251908396946565, 'imitation_auc': 0.4751908396946565, 'optimal_acc': 0.8911564625

______epoch 52 _____
val reward 0.46951669454574585
imitation reward 1.1000232696533203
distance losses 5.492725372314453 1.2029422521591187
distributions [0.8779140114784241, 0.028962677344679832, 0.0650019496679306]
[{'decision': 0, 'optimal_auc': 0.8606870229007634, 'imitation_auc': 0.5166984732824427, 'optimal_acc': 0.891156462585034, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.7350543478260869, 'optimal_acc': 1.0, 'imitation_acc': 0.782312925170068}, {'decision': 2, 'optimal_auc': 0.9469424460431655, 'imitation_auc': 0.7460267005721553, 'optimal_acc': 0.9455782312925171, 'imitation_acc': 0.8231292517006803}]
______epoch 53 _____
val reward 0.46571114659309387
imitation reward 1.0989162921905518
distance losses 5.7221574783325195 1.1785507202148438
distributions [0.8777611255645752, 0.028379764407873154, 0.06553095579147339]
[{'decision': 0, 'optimal_auc': 0.870706106870229, 'imitation_auc': 0.5252862595419847, 'optimal_acc': 0.8911564

...

______epoch 78 _____
val reward 0.37743186950683594
imitation reward 1.0889043807983398
distance losses 5.6104044914245605 1.2043993473052979
distributions [0.8753675818443298, 0.0191310066729784, 0.06929043680429459]
[{'decision': 0, 'optimal_auc': 0.9541984732824427, 'imitation_auc': 0.5920801526717557, 'optimal_acc': 0.9115646258503401, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.6964673913043478, 'optimal_acc': 1.0, 'imitation_acc': 0.782312925170068}, {'decision': 2, 'optimal_auc': 0.9595323741007193, 'imitation_auc': 0.7492053401144311, 'optimal_acc': 0.9455782312925171, 'imitation_acc': 0.8231292517006803}]
______epoch 79 _____
val reward 0.37481915950775146
imitation reward 1.088160514831543
distance losses 5.4727864265441895 1.3375747203826904
distributions [0.8758946657180786, 0.018922362476587296, 0.0691092237830162]
[{'decision': 0, 'optimal_auc': 0.9541984732824427, 'imitation_auc': 0.5930343511450381, 'optimal_acc': 0.9115646

______epoch 91 _____
val reward 0.3435291349887848
imitation reward 1.069589614868164
distance losses 5.113526821136475 1.2245979309082031
distributions [0.8776054382324219, 0.017030715942382812, 0.07023125141859055]
[{'decision': 0, 'optimal_auc': 0.9527671755725191, 'imitation_auc': 0.612118320610687, 'optimal_acc': 0.9183673469387755, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.70625, 'optimal_acc': 1.0, 'imitation_acc': 0.7891156462585034}, {'decision': 2, 'optimal_auc': 0.9613309352517985, 'imitation_auc': 0.7832167832167832, 'optimal_acc': 0.9591836734693877, 'imitation_acc': 0.8231292517006803}]
______epoch 92 _____
val reward 0.3407333493232727
imitation reward 1.0696865320205688
distance losses 5.56345796585083 0.9336056709289551
distributions [0.8777164816856384, 0.016899272799491882, 0.0700165331363678]
[{'decision': 0, 'optimal_auc': 0.9537213740458015, 'imitation_auc': 0.612118320610687, 'optimal_acc': 0.9183673469387755, 'imi

______epoch 104 _____
val reward 0.31849223375320435
imitation reward 1.0812848806381226
distance losses 5.4181294441223145 1.2462717294692993
distributions [0.8825017213821411, 0.01581139862537384, 0.06637956202030182]
[{'decision': 0, 'optimal_auc': 0.958969465648855, 'imitation_auc': 0.5973282442748091, 'optimal_acc': 0.9251700680272109, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.6663043478260869, 'optimal_acc': 1.0, 'imitation_acc': 0.782312925170068}, {'decision': 2, 'optimal_auc': 0.9658273381294964, 'imitation_auc': 0.7752701843610934, 'optimal_acc': 0.9523809523809523, 'imitation_acc': 0.8231292517006803}]
______epoch 105 _____
val reward 0.31649819016456604
imitation reward 1.0810288190841675
distance losses 5.3610520362854 1.1661831140518188
distributions [0.8821842670440674, 0.015762563794851303, 0.06694407016038895]
[{'decision': 0, 'optimal_auc': 0.9594465648854962, 'imitation_auc': 0.5911259541984732, 'optimal_acc': 0.925170

______epoch 117 _____
val reward 0.3006199896335602
imitation reward 1.0883839130401611
distance losses 5.246136665344238 1.122463345527649
distributions [0.8848807215690613, 0.014896991662681103, 0.06498200446367264]
[{'decision': 0, 'optimal_auc': 0.95706106870229, 'imitation_auc': 0.5858778625954199, 'optimal_acc': 0.9387755102040817, 'imitation_acc': 0.891156462585034}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.672554347826087, 'optimal_acc': 1.0, 'imitation_acc': 0.7959183673469388}, {'decision': 2, 'optimal_auc': 0.9640287769784173, 'imitation_auc': 0.7813095994914177, 'optimal_acc': 0.9591836734693877, 'imitation_acc': 0.8095238095238095}]
______epoch 118 _____
val reward 0.2992367744445801
imitation reward 1.090163230895996
distance losses 5.80535364151001 1.2133219242095947
distributions [0.8853470087051392, 0.0148167060688138, 0.06430988013744354]
[{'decision': 0, 'optimal_auc': 0.9575381679389313, 'imitation_auc': 0.5873091603053435, 'optimal_acc': 0.938775510204

DecisionModel(
  (input_dropout): Dropout(p=0.25, inplace=False)
  (layers): ModuleList(
    (0): Linear(in_features=90, out_features=500, bias=True)
    (1): ReLU()
  )
  (batchnorm): BatchNorm1d(500, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (dropout): Dropout(p=0.25, inplace=False)
  (relu): Softplus(beta=1, threshold=20)
  (sigmoid): Sigmoid()
  (softmax): LogSoftmax(dim=1)
  (final_opt_layer): Linear(in_features=500, out_features=20, bias=True)
  (final_imitation_layer): Linear(in_features=500, out_features=20, bias=True)
  (final_layer): Linear(in_features=40, out_features=6, bias=True)
)

In [ ]:
# for iteration in range(10):
#     tempmodel, tempscore,temploss,_ = train_decision_model(
#         emodel1,emodel2,emodel3,
#         lr=.001,
#         use_attention=True,
#         imitation_weight=1,
#         reward_weight=1,
#         validate_with_memory=True,
#         use_smote=False,
#         verbose=False,
#         threshold_decisions=False,
#         **args)
#     if temploss < decision_loss:
#         print('new best',tempscore)
#         print('vs',decision_score)
#         decision_model = tempmodel
#         decision_score = tempscore
#         decision_loss = temploss

In [ ]:
def gridsearch_triplet_model(m1,m2,m3,weights=[-1,1,1,-1]):
    hidden_layers = [[50],[100],[200],[500],[1000]]
    extra_layers = [20,50,100,200]
    best_loss = 100000000000
    best_metrics = {}
    best_args = {}
    best_model = None
    best_record = {}
    k = 0
    records = []
    for hl in hidden_layers:
        for el in extra_layers:
            args = {'hidden_layers': hl, 'opt_layer_size': el, 'imitation_layer_size': el}
            for dropout in [.1,.25,.5,.75]:
                args['dropout'] = dropout
                for input_dropout in [0.1,.25,.5]:
                    args['input_dropout'] = input_dropout
                    for shufflecol_chance in [.1,.5]:
                        try:
                            args['shufflecol_chance'] = shufflecol_chance
                            model,m_metrics,m_loss,m_distribution = train_decision_model_triplet(m1,m2,m3,
                                                                        lr=.01,
                                                                        weights=weights,
                                                                        verbose=False,
                                                                        **args)
                            entry = {
                                'metrics': m_metrics,
                                'loss': m_loss,
                                'args': args,
                                'distribution': m_distribution,
                            }
                            records.append(entry)
                            print('done',k,m_loss)
                            print('curr best',best_loss)
                            k+=1
                            if m_loss < best_loss:
                                best_loss = m_loss
                                best_metrics  = m_metrics
                                best_model = model
                                best_args = args
                                best_record = entry
                                print('_++++++++++New Best++++____')
                                print(best_loss)
                                print(best_metrics)
                                print(best_args)
                                print('___________')
                                print('++++++++')
                                print()
                        except Exception as e:
                            print('error',e,args)
    print('_________')
    print('+++++++++++')
    print('best stuff',best_loss)
    print(best_metrics)
    print(best_args)
    return best_model, records, best_record

decision_model_best,records, bestr = gridsearch_triplet_model(emodel1,emodel2,emodel3,weights=[-1,1,1,-1])
records

++++++++++Final+++++++++++
best tensor(1.1372, grad_fn=<AddBackward0>)
[{'decision': 0, 'optimal_auc': 0.9341603053435115, 'imitation_auc': 0.5391221374045801, 'optimal_acc': 0.9455782312925171, 'imitation_acc': 0.9047619047619048}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.6842391304347827, 'optimal_acc': 1.0, 'imitation_acc': 0.7755102040816326}, {'decision': 2, 'optimal_auc': 0.9730215827338129, 'imitation_auc': 0.7180546726001272, 'optimal_acc': 0.9659863945578231, 'imitation_acc': 0.7959183673469388}]
done 0 tensor(1.1372, grad_fn=<AddBackward0>)
curr best 100000000000
_++++++++++New Best++++____
tensor(1.1372, grad_fn=<AddBackward0>)
[{'decision': 0, 'optimal_auc': 0.9341603053435115, 'imitation_auc': 0.5391221374045801, 'optimal_acc': 0.9455782312925171, 'imitation_acc': 0.9047619047619048}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.6842391304347827, 'optimal_acc': 1.0, 'imitation_acc': 0.7755102040816326}, {'decision': 2, 'optimal_auc': 0.973021582733812

++++++++++Final+++++++++++
best tensor(1.0312, grad_fn=<AddBackward0>)
[{'decision': 0, 'optimal_auc': 0.9642175572519084, 'imitation_auc': 0.5572519083969466, 'optimal_acc': 0.9251700680272109, 'imitation_acc': 0.8775510204081632}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.7472826086956521, 'optimal_acc': 1.0, 'imitation_acc': 0.7891156462585034}, {'decision': 2, 'optimal_auc': 0.9802158273381295, 'imitation_auc': 0.8057851239669422, 'optimal_acc': 0.9863945578231292, 'imitation_acc': 0.8231292517006803}]
done 8 tensor(1.0312, grad_fn=<AddBackward0>)
curr best tensor(1.0471, grad_fn=<AddBackward0>)
_++++++++++New Best++++____
tensor(1.0312, grad_fn=<AddBackward0>)
[{'decision': 0, 'optimal_auc': 0.9642175572519084, 'imitation_auc': 0.5572519083969466, 'optimal_acc': 0.9251700680272109, 'imitation_acc': 0.8775510204081632}, {'decision': 1, 'optimal_auc': -1, 'imitation_auc': 0.7472826086956521, 'optimal_acc': 1.0, 'imitation_acc': 0.7891156462585034}, {'decision': 2, 'optim

In [159]:
bestr

NameError: name 'bestr' is not defined

In [ ]:
# torch.save(model1,'../data/models/final_transition1_model_' + emodel1.identifier + '.pt')
# torch.save(model2,'../data/models/final_transition2_model_' + emodel2.identifier + '.pt')
# torch.save(model3,'../data/models/final_outcome_model_' + emodel3.identifier + '.pt')
# print('../data/models/final_transition1_model_' + emodel1.identifier + '.pt')
# print('../data/models/final_transition2_model_' + emodel2.identifier + '.pt')
# print('../data/models/final_outcome_model_' + emodel3.identifier + '.pt')

In [157]:
decision_model.set_device('cpu')
emodel1.set_device('cpu')
emodel2.set_device('cpu')
emodel3.set_device('cpu')
torch.save(decision_model,'../resources/decision_model.pt')
torch.save(emodel1,'../resources/transition1_model.pt')
torch.save(emodel2,'../resources/transition2_model.pt')
torch.save(emodel3,'../resources/outcome_model.pt')

In [ ]:
def get_default_predictions(dm):
    res  = []
    for state in [0,1,2]:
        mem = dm.memory[state]
        mem = torch.median(mem,dim=0)[0].type(torch.FloatTensor)
        val = dm(mem.reshape(1,-1),position=state)
        res.append(val.cpu().detach().numpy())
    return np.stack(res)
get_default_predictions(decision_model)